In [6]:
import os
####*IMPORANT*: Have to do this line *before* importing tensorflow
os.environ['PYTHONHASHSEED']=str(1)
import numpy as np
import tensorflow as tf
import random

# Use scikit-learn to grid search the batch size and epochs
import numpy
from sklearn.model_selection import GridSearchCV
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.wrappers.scikit_learn import KerasRegressor

# Function to create model, required for KerasClassifier
from math import sqrt
from numpy import concatenate
from matplotlib import pyplot
from pandas import read_csv
from pandas import DataFrame
from pandas import concat
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_squared_error
from tensorflow.keras.layers import LSTM
import keras

def reset_random_seeds():
   os.environ['PYTHONHASHSEED']=str(1)
   tf.random.set_seed(1)
   np.random.seed(1)
   random.seed(1)

#make some random data
reset_random_seeds()
#np.random.rand(4)

In [7]:
# design network
def create_model():
    model = Sequential()
    model.add(LSTM(50,return_sequences=True, input_shape=(train_X.shape[1], train_X.shape[2])))
    model.add(LSTM(50))
    model.add(Dense(10))
    model.add(Dense(1,kernel_initializer='normal'))#, kernel_initializer='normal'
    #mse or mae it got better with mae
    model.compile(loss='mae', optimizer='adam')
    return model

In [8]:
#define the grid search parameters    
batch_size = [1, 4, 8, 10, 16, 18, 24, 32]
epochs = [100, 200, 300, 400, 500]
param_grid = dict(batch_size=batch_size, epochs=epochs)

In [9]:
# fix random seed for reproducibility
reset_random_seeds()
#numpy.random.rand(4)

In [10]:
# convert series to supervised learning
def series_to_supervised(data, n_in=1, n_out=1, dropnan=True):
    n_vars = 1 if type(data) is list else data.shape[1]
    df = DataFrame(data)
    cols, names = list(), list()
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
        cols.append(df.shift(i))
        names += [('var%d(t-%d)' % (j+1, i)) for j in range(n_vars)]
    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df.shift(-i))
        if i == 0:
            names += [('var%d(t)' % (j+1)) for j in range(n_vars)]
        else:
            names += [('var%d(t+%d)' % (j+1, i)) for j in range(n_vars)]
    # put it all together
    agg = concat(cols, axis=1)
    agg.columns = names
    # drop rows with NaN values
    if dropnan:
        agg.dropna(inplace=True)
    return agg

In [11]:
# load dataset
dataset = read_csv('C:/Users/*', header=0, index_col=0)
values = dataset.values

# ensure all data is float
values = values.astype('float32')

# normalize features
scaler = MinMaxScaler(feature_range=(0, 1))
scaled = scaler.fit_transform(values)

# specify the number of lag hours
n_hours = 7
n_features = 9

# frame as supervised learning
reframed = series_to_supervised(scaled, n_hours, 1)
print(reframed.shape)

reframed

(3753, 72)


var1(t-7)  var2(t-7)  var3(t-7)  var4(t-7)  var5(t-7)  var6(t-7)  \
7      0.102253   0.344225   0.496861   0.432082   0.473684   0.416821   
8      0.102253   0.473141   0.569541   0.583276   0.467105   0.343693   
9      0.098787   0.545438   0.688471   0.792150   0.467105   0.305302   
10     0.094454   0.349753   0.833168   0.781570   0.552632   0.308960   
11     0.105719   0.144074   0.817311   0.697611   0.572368   0.295250   
...         ...        ...        ...        ...        ...        ...   
3755   0.530329   0.366648   0.717542   0.555631   0.631579   0.425961   
3756   0.489601   0.162930   0.773704   0.523549   0.638158   0.286106   
3757   0.504333   0.163181   0.683515   0.401706   0.717105   0.297993   
3758   0.452340   0.211124   0.663694   0.509556   0.585526   0.354664   
3759   0.665511   0.157377   0.699372   0.539249   0.526316   0.260513   

         var7(t-7)  var8(t-7)  var9(t-7)  var1(t-6)  ...  var9(t-1)   var1(t)  \
7     3.553964e-04   0.459406   0.508801   0.102253  ...   0.632959  0.142114   
8     3.553964e-04   0.523763   0.575999   0.098787  ...   0.611199  0.094454   
9     3.553964e-04   0.666666   0.661760   0.094454  ...   0.647360  0.103120   
10    3.553964e-04   0.821452   0.806721   0.105719  ...   0.790400  0.124783   
11    3.553964e-04   0.832344   0.796160   0.113518  ...   0.716160  0.118718   
...            ...        ...        ...        ...  ...        ...       ...   
3755  8.269736e-07   0.670628   0.718400   0.489601  ...   0.472960  0.558925   
3756  8.269736e-07   0.801980   0.774400   0.504333  ...   0.574720  0.626516   
3757  1.775448e-03   0.672277   0.664000   0.452340  ...   0.598721  0.595321   
3758  8.269736e-07   0.663367   0.673920   0.665511  ...   0.632959  0.509532   
3759  8.269736e-07   0.684488   0.680320   0.634315  ...   0.590720  0.579723   

       var2(t)   var3(t)   var4(t)   var5(t)   var6(t)       var7(t)  \
7     0.188230  0.639908  0.595904  0.500000  0.372944  3.553964e-04   
8     0.270994  0.672944  0.612628  0.513158  0.432362  3.553964e-04   
9     0.066146  0.857944  0.589420  0.473684  0.190128  3.553964e-04   
10    0.276981  0.630988  0.471331  0.493421  0.207497  3.553964e-04   
11    0.213220  0.604559  0.551877  0.480263  0.210239  3.553964e-04   
...        ...       ...       ...       ...       ...           ...   
3755  0.252665  0.583086  0.449488  0.539474  0.377514  8.269736e-07   
3756  0.155024  0.588701  0.377474  0.578947  0.377514  8.269736e-07   
3757  0.135852  0.643210  0.363823  0.631579  0.393055  8.269736e-07   
3758  0.141195  0.608523  0.439249  0.552632  0.354664  8.269736e-07   
3759  0.157297  0.561612  0.349147  0.592105  0.393055  8.269736e-07   

       var8(t)   var9(t)  
7     0.644885  0.611199  
8     0.659077  0.647360  
9     0.843895  0.790400  
10    0.601980  0.716160  
11    0.597361  0.595200  
...        ...       ...  
3755  0.563367  0.574720  
3756  0.597361  0.598721  
3757  0.609571  0.632959  
3758  0.624422  0.590720  
3759  0.533663  0.576320  

[3753 rows x 72 columns]

In [12]:
# split into train and test sets
values = reframed.values
n_train_hours = 1925
train = values[:n_train_hours, :]
test = values[n_train_hours:, :]
# split into input and outputs
n_obs = n_hours * n_features
train_X, train_y = train[:, :n_obs], train[:, -n_features]
test_X, test_y = test[:, :n_obs], test[:, -n_features]
print(train_X.shape, len(train_X), train_y.shape)
# reshape input to be 3D [samples, timesteps, features]
train_X = train_X.reshape((train_X.shape[0], n_hours, n_features))
test_X = test_X.reshape((test_X.shape[0], n_hours, n_features))
print(train_X.shape, train_y.shape, test_X.shape, test_y.shape)

(1925, 63) 1925 (1925,)
(1925, 7, 9) (1925,) (1828, 7, 9) (1828,)


In [13]:
reframed

var1(t-7)  var2(t-7)  var3(t-7)  var4(t-7)  var5(t-7)  var6(t-7)  \
7      0.102253   0.344225   0.496861   0.432082   0.473684   0.416821   
8      0.102253   0.473141   0.569541   0.583276   0.467105   0.343693   
9      0.098787   0.545438   0.688471   0.792150   0.467105   0.305302   
10     0.094454   0.349753   0.833168   0.781570   0.552632   0.308960   
11     0.105719   0.144074   0.817311   0.697611   0.572368   0.295250   
...         ...        ...        ...        ...        ...        ...   
3755   0.530329   0.366648   0.717542   0.555631   0.631579   0.425961   
3756   0.489601   0.162930   0.773704   0.523549   0.638158   0.286106   
3757   0.504333   0.163181   0.683515   0.401706   0.717105   0.297993   
3758   0.452340   0.211124   0.663694   0.509556   0.585526   0.354664   
3759   0.665511   0.157377   0.699372   0.539249   0.526316   0.260513   

         var7(t-7)  var8(t-7)  var9(t-7)  var1(t-6)  ...  var9(t-1)   var1(t)  \
7     3.553964e-04   0.459406   0.508801   0.102253  ...   0.632959  0.142114   
8     3.553964e-04   0.523763   0.575999   0.098787  ...   0.611199  0.094454   
9     3.553964e-04   0.666666   0.661760   0.094454  ...   0.647360  0.103120   
10    3.553964e-04   0.821452   0.806721   0.105719  ...   0.790400  0.124783   
11    3.553964e-04   0.832344   0.796160   0.113518  ...   0.716160  0.118718   
...            ...        ...        ...        ...  ...        ...       ...   
3755  8.269736e-07   0.670628   0.718400   0.489601  ...   0.472960  0.558925   
3756  8.269736e-07   0.801980   0.774400   0.504333  ...   0.574720  0.626516   
3757  1.775448e-03   0.672277   0.664000   0.452340  ...   0.598721  0.595321   
3758  8.269736e-07   0.663367   0.673920   0.665511  ...   0.632959  0.509532   
3759  8.269736e-07   0.684488   0.680320   0.634315  ...   0.590720  0.579723   

       var2(t)   var3(t)   var4(t)   var5(t)   var6(t)       var7(t)  \
7     0.188230  0.639908  0.595904  0.500000  0.372944  3.553964e-04   
8     0.270994  0.672944  0.612628  0.513158  0.432362  3.553964e-04   
9     0.066146  0.857944  0.589420  0.473684  0.190128  3.553964e-04   
10    0.276981  0.630988  0.471331  0.493421  0.207497  3.553964e-04   
11    0.213220  0.604559  0.551877  0.480263  0.210239  3.553964e-04   
...        ...       ...       ...       ...       ...           ...   
3755  0.252665  0.583086  0.449488  0.539474  0.377514  8.269736e-07   
3756  0.155024  0.588701  0.377474  0.578947  0.377514  8.269736e-07   
3757  0.135852  0.643210  0.363823  0.631579  0.393055  8.269736e-07   
3758  0.141195  0.608523  0.439249  0.552632  0.354664  8.269736e-07   
3759  0.157297  0.561612  0.349147  0.592105  0.393055  8.269736e-07   

       var8(t)   var9(t)  
7     0.644885  0.611199  
8     0.659077  0.647360  
9     0.843895  0.790400  
10    0.601980  0.716160  
11    0.597361  0.595200  
...        ...       ...  
3755  0.563367  0.574720  
3756  0.597361  0.598721  
3757  0.609571  0.632959  
3758  0.624422  0.590720  
3759  0.533663  0.576320  

[3753 rows x 72 columns]

In [14]:
# drop columns we don't want to predict
#reframed.drop(reframed.columns[[55,56,57,58,59,60,61,62]], axis=1, inplace=True)
reframed.drop(reframed.columns[[64,65,66,67,68,69,70,71]], axis=1, inplace=True)
print(reframed.head())

    var1(t-7)  var2(t-7)  var3(t-7)  var4(t-7)  var5(t-7)  var6(t-7)  \
7    0.102253   0.344225   0.496861   0.432082   0.473684   0.416821   
8    0.102253   0.473141   0.569541   0.583276   0.467105   0.343693   
9    0.098787   0.545438   0.688471   0.792150   0.467105   0.305302   
10   0.094454   0.349753   0.833168   0.781570   0.552632   0.308960   
11   0.105719   0.144074   0.817311   0.697611   0.572368   0.295250   

    var7(t-7)  var8(t-7)  var9(t-7)  var1(t-6)  ...  var1(t-1)  var2(t-1)  \
7    0.000355   0.459406   0.508801   0.102253  ...   0.079723   0.302286   
8    0.000355   0.523763   0.575999   0.098787  ...   0.142114   0.188230   
9    0.000355   0.666666   0.661760   0.094454  ...   0.094454   0.270994   
10   0.000355   0.821452   0.806721   0.105719  ...   0.103120   0.066146   
11   0.000355   0.832344   0.796160   0.113518  ...   0.124783   0.276981   

    var3(t-1)  var4(t-1)  var5(t-1)  var6(t-1)  var7(t-1)  var8(t-1)  \
7    0.612488   0.495222   0.559

In [15]:
# create model
model = KerasRegressor(build_fn=create_model, verbose=1)

In [ ]:
#from sklearn.model_selection import TimeSeriesSplit
#tscv = TimeSeriesSplit(n_splits=3)
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_squared_error')
#grid_result = grid.fit(train_X, train_y)

from sklearn.model_selection import TimeSeriesSplit
tscv = TimeSeriesSplit(n_splits=3)

grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_squared_error')
grid_result = grid.fit(train_X, train_y)

Train on 482 samples
Epoch 1/100
482/482 [==============================] - 12s 25ms/sample - loss: 0.0309
Epoch 2/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0291
Epoch 3/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0282
Epoch 4/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0272
Epoch 5/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0262
Epoch 6/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0263
Epoch 7/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0260
Epoch 8/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0247
Epoch 9/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0237
Epoch 10/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0240
Epoch 11/100
482/482 [==============================] - 5s 11ms/sample - loss: 0.0228
Epoch 12/100
482/482 [===================

963/963 [==============================] - 10s 10ms/sample - loss: 0.0183
Epoch 89/100
963/963 [==============================] - 11s 11ms/sample - loss: 0.0181
Epoch 90/100
963/963 [==============================] - 10s 11ms/sample - loss: 0.0181
Epoch 91/100
963/963 [==============================] - 10s 11ms/sample - loss: 0.0181
Epoch 92/100
963/963 [==============================] - 10s 11ms/sample - loss: 0.0178
Epoch 93/100
963/963 [==============================] - 10s 11ms/sample - loss: 0.0180
Epoch 94/100
963/963 [==============================] - 11s 12ms/sample - loss: 0.0181
Epoch 95/100
963/963 [==============================] - 11s 12ms/sample - loss: 0.0178
Epoch 96/100
963/963 [==============================] - 11s 11ms/sample - loss: 0.0179
Epoch 97/100
963/963 [==============================] - 11s 12ms/sample - loss: 0.0177
Epoch 98/100
963/963 [==============================] - 11s 11ms/sample - loss: 0.0180
Epoch 99/100
963/963 [==============================] - 

482/482 [==============================] - 3s 7ms/sample - loss: 0.0186
Epoch 75/200
482/482 [==============================] - 3s 7ms/sample - loss: 0.0188
Epoch 76/200
482/482 [==============================] - 3s 7ms/sample - loss: 0.0184
Epoch 77/200
482/482 [==============================] - 3s 7ms/sample - loss: 0.0184
Epoch 78/200
482/482 [==============================] - 3s 7ms/sample - loss: 0.0183
Epoch 79/200
482/482 [==============================] - 4s 8ms/sample - loss: 0.0179
Epoch 80/200
482/482 [==============================] - 4s 7ms/sample - loss: 0.0183
Epoch 81/200
482/482 [==============================] - 4s 8ms/sample - loss: 0.0178
Epoch 82/200
482/482 [==============================] - 4s 7ms/sample - loss: 0.0175
Epoch 83/200
482/482 [==============================] - 4s 7ms/sample - loss: 0.0180
Epoch 84/200
482/482 [==============================] - 4s 8ms/sample - loss: 0.0179
Epoch 85/200
482/482 [==============================] - 4s 8ms/sample - loss: 

963/963 [==============================] - 5s 5ms/sample - loss: 0.0201
Epoch 65/200
963/963 [==============================] - 5s 5ms/sample - loss: 0.0204
Epoch 66/200
963/963 [==============================] - 5s 5ms/sample - loss: 0.0203
Epoch 67/200
963/963 [==============================] - 5s 5ms/sample - loss: 0.0203
Epoch 68/200
963/963 [==============================] - 5s 5ms/sample - loss: 0.0197
Epoch 69/200
963/963 [==============================] - 5s 5ms/sample - loss: 0.0203
Epoch 70/200
963/963 [==============================] - 5s 5ms/sample - loss: 0.0200
Epoch 71/200
963/963 [==============================] - 4s 5ms/sample - loss: 0.0201
Epoch 72/200
963/963 [==============================] - 5s 5ms/sample - loss: 0.0200
Epoch 73/200
963/963 [==============================] - 5s 5ms/sample - loss: 0.0195
Epoch 74/200
963/963 [==============================] - 5s 5ms/sample - loss: 0.0197
Epoch 75/200
963/963 [==============================] - 5s 5ms/sample - loss: 

1444/1444 [==============================] - 10s 7ms/sample - loss: 0.0224
Epoch 53/200
1444/1444 [==============================] - 10s 7ms/sample - loss: 0.0225
Epoch 54/200
1444/1444 [==============================] - 10s 7ms/sample - loss: 0.0219
Epoch 55/200
1444/1444 [==============================] - 10s 7ms/sample - loss: 0.0223
Epoch 56/200
1444/1444 [==============================] - 10s 7ms/sample - loss: 0.0216
Epoch 57/200
1444/1444 [==============================] - 10s 7ms/sample - loss: 0.0216
Epoch 58/200
1444/1444 [==============================] - ETA: 0s - loss: 0.022 - 10s 7ms/sample - loss: 0.0219
Epoch 59/200
1444/1444 [==============================] - 10s 7ms/sample - loss: 0.0215
Epoch 60/200
1444/1444 [==============================] - 10s 7ms/sample - loss: 0.0215
Epoch 61/200
1444/1444 [==============================] - 9s 6ms/sample - loss: 0.0218
Epoch 62/200
1444/1444 [==============================] - 9s 6ms/sample - loss: 0.0217
Epoch 63/200
1444/1444 

...

1444/1444 [==============================] - 1s 969us/sample - loss: 0.0222
Epoch 83/100
1444/1444 [==============================] - 2s 1ms/sample - loss: 0.0223
Epoch 84/100
1444/1444 [==============================] - 1s 1ms/sample - loss: 0.0224
Epoch 85/100
1444/1444 [==============================] - 1s 869us/sample - loss: 0.0223
Epoch 86/100
1444/1444 [==============================] - 1s 867us/sample - loss: 0.0220
Epoch 87/100
1444/1444 [==============================] - 1s 908us/sample - loss: 0.0213
Epoch 88/100
1444/1444 [==============================] - 1s 892us/sample - loss: 0.0220
Epoch 89/100
1444/1444 [==============================] - 1s 899us/sample - loss: 0.0223
Epoch 90/100
1444/1444 [==============================] - 1s 831us/sample - loss: 0.0219
Epoch 91/100
1444/1444 [==============================] - 1s 840us/sample - loss: 0.0216
Epoch 92/100
1444/1444 [==============================] - 1s 820us/sample - loss: 0.0217
Epoch 93/100
1444/1444 [==============

482/482 [==============================] - 1s 2ms/sample - loss: 0.0188
Epoch 168/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0199
Epoch 169/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0182
Epoch 170/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0178
Epoch 171/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0184
Epoch 172/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0177
Epoch 173/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0181
Epoch 174/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0188 0s - 
Epoch 175/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0189
Epoch 176/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0175
Epoch 177/200
482/482 [==============================] - 1s 2ms/sample - loss: 0.0178
Epoch 178/200
482/482 [==============================] - 1s 2m

Epoch 62/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0223
Epoch 63/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0216
Epoch 64/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0220
Epoch 65/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0219
Epoch 66/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0228
Epoch 67/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0221
Epoch 68/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0219
Epoch 69/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0223
Epoch 70/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0216
Epoch 71/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0219
Epoch 72/200
963/963 [==============================] - 2s 2ms/sample - loss: 0.0215
Epoch 73/200
963/963 [==============================] - 2s 2ms/sa

1444/1444 [==============================] - 3s 2ms/sample - loss: 0.0247
Epoch 51/200
1444/1444 [==============================] - 3s 2ms/sample - loss: 0.0244
Epoch 52/200
1444/1444 [==============================] - 2s 2ms/sample - loss: 0.0249
Epoch 53/200
1444/1444 [==============================] - 3s 2ms/sample - loss: 0.0246
Epoch 54/200
1444/1444 [==============================] - 2s 2ms/sample - loss: 0.0245
Epoch 55/200
1444/1444 [==============================] - 2s 2ms/sample - loss: 0.0238
Epoch 56/200
1444/1444 [==============================] - 2s 2ms/sample - loss: 0.0245
Epoch 57/200
1444/1444 [==============================] - 2s 2ms/sample - loss: 0.0243
Epoch 58/200
1444/1444 [==============================] - 2s 2ms/sample - loss: 0.0238
Epoch 59/200
1444/1444 [==============================] - 2s 2ms/sample - loss: 0.0233
Epoch 60/200
1444/1444 [==============================] - 3s 2ms/sample - loss: 0.0233
Epoch 61/200
1444/1444 [==============================] 

482/482 [==============================] - 1s 2ms/sample - loss: 0.0214
Epoch 36/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0207
Epoch 37/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0217
Epoch 38/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0207
Epoch 39/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0215
Epoch 40/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0200
Epoch 41/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0208
Epoch 42/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0205
Epoch 43/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0217
Epoch 44/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0199
Epoch 45/300
482/482 [==============================] - 1s 2ms/sample - loss: 0.0207
Epoch 46/300
482/482 [==============================] - 1s 2ms/sample - loss: 

In [ ]:
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

In [13]:
import os
####*IMPORANT*: Have to do this line *before* importing tensorflow
os.environ['PYTHONHASHSEED']=str(1)
import numpy as np
import tensorflow as tf
import random

# Use scikit-learn to grid search the batch size and epochs
import numpy
from sklearn.model_selection import GridSearchCV
from tensorflow.keras.models import Sequential 
from tensorflow.keras.layers import Dense
from tensorflow.keras.wrappers.scikit_learn import KerasRegressor

# Function to create model, required for KerasClassifier
from math import sqrt
from numpy import concatenate
from matplotlib import pyplot
from pandas import read_csv
from pandas import DataFrame
from pandas import concat
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_squared_error
from tensorflow.keras.layers import LSTM
import keras

def reset_random_seeds():
   os.environ['PYTHONHASHSEED']=str(1)
   tf.random.set_seed(1)
   np.random.seed(1)
   random.seed(1)

#make some random data
reset_random_seeds()
#np.random.rand(4)


# design network
def create_model(optimizer='adam'):
    model = Sequential()
    model.add(LSTM(50, return_sequences=True, input_shape=(train_X.shape[1], train_X.shape[2])))
    model.add(LSTM(50))
    model.add(Dense(10))
    model.add(Dense(1))
    #mse or mae it got better with mae
    model.compile(loss='mae', optimizer=optimizer)
    return model

In [14]:
optimizer = ['SGD', 'RMSprop', 'Adagrad', 'Adadelta', 'Adam', 'Adamax', 'Nadam']
param_grid = dict(optimizer=optimizer)

In [15]:
# fix random seed for reproducibility
seed = 1 #seed 7
numpy.random.seed(seed)
#numpy.random.rand(4)

# convert series to supervised learning
def series_to_supervised(data, n_in=1, n_out=1, dropnan=True):
    n_vars = 1 if type(data) is list else data.shape[1]
    df = DataFrame(data)
    cols, names = list(), list()
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
        cols.append(df.shift(i))
        names += [('var%d(t-%d)' % (j+1, i)) for j in range(n_vars)]
    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df.shift(-i))
        if i == 0:
            names += [('var%d(t)' % (j+1)) for j in range(n_vars)]
        else:
            names += [('var%d(t+%d)' % (j+1, i)) for j in range(n_vars)]
    # put it all together
    agg = concat(cols, axis=1)
    agg.columns = names
    # drop rows with NaN values
    if dropnan:
        agg.dropna(inplace=True)
    return agg

In [16]:
# load dataset
dataset = read_csv('C:/Users/*', header=0, index_col=0)
values = dataset.values

# ensure all data is float
values = values.astype('float32')

# normalize features
scaler = MinMaxScaler(feature_range=(0, 1))
scaled = scaler.fit_transform(values)

# specify the number of lag hours
n_hours = 2
n_features = 9

# frame as supervised learning
reframed = series_to_supervised(scaled, n_hours, 1)
print(reframed.shape)

reframed

(535, 27)


var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2     0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3     0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4     0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5     0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6     0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   
..         ...        ...        ...        ...        ...        ...   
532   0.647471   0.350071   0.683410   0.600138   0.604167   0.304962   
533   0.624708   0.579207   0.717050   0.770611   0.531250   0.351837   
534   0.797471   0.478075   0.801382   0.687265   0.781250   0.186211   
535   0.766732   0.534690   0.864055   0.749342   0.687500   0.286762   
536   0.690856   0.608430   0.800000   0.597099   0.791667   0.308640   

     var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  ...  var9(t-1)   var1(t)  \
2     0.001171   0.706132   0.735252   0.055642  ...   0.697631  0.075875   
3     0.000861   0.674529   0.697631   0.075875  ...   0.797491  0.103307   
4     0.000861   0.823113   0.797491   0.103307  ...   0.810961  0.176265   
5     0.003931   0.802359   0.810961   0.176265  ...   0.823037  0.143191   
6     0.001171   0.840095   0.823037   0.143191  ...   0.573618  0.144163   
..         ...        ...        ...        ...  ...        ...       ...   
532   0.015390   0.658019   0.671620   0.624708  ...   0.698095  0.797471   
533   0.000002   0.708019   0.698095   0.797471  ...   0.819786  0.766732   
534   0.075827   0.788679   0.819786   0.766732  ...   0.856014  0.690856   
535   0.000002   0.866982   0.856014   0.690856  ...   0.820714  0.663813   
536   0.090269   0.780190   0.820714   0.663813  ...   0.826753  0.792801   

      var2(t)   var3(t)   var4(t)   var5(t)   var6(t)   var7(t)   var8(t)  \
2    0.675534  0.822119  0.834066  0.541667  0.329227  0.000861  0.823113   
3    0.721197  0.808756  0.800696  0.677083  0.259926  0.003931  0.802359   
4    0.554569  0.833639  0.748459  0.697917  0.157902  0.001171  0.840095   
5    0.288067  0.575576  0.597859  0.500000  0.110291  0.190853  0.546227   
6    0.366840  0.649308  0.503348  0.656250  0.150917  0.132394  0.598114   
..        ...       ...       ...       ...       ...       ...       ...   
532  0.478075  0.801382  0.687265  0.781250  0.186211  0.075827  0.788679   
533  0.534690  0.864055  0.749342  0.687500  0.286762  0.000002  0.866982   
534  0.608430  0.800000  0.597099  0.791667  0.308640  0.090269  0.780190   
535  0.418575  0.819816  0.612433  0.729167  0.255695  0.000616  0.825472   
536  0.317628  0.627189  0.454131  0.572917  0.294670  0.002762  0.609907   

      var9(t)  
2    0.797491  
3    0.810961  
4    0.823037  
5    0.573618  
6    0.680910  
..        ...  
532  0.819786  
533  0.856014  
534  0.820714  
535  0.826753  
536  0.631677  

[535 rows x 27 columns]

In [17]:
# split into train and test sets
values = reframed.values
n_train_hours = 400
train = values[:n_train_hours, :]
test = values[n_train_hours:, :]
# split into input and outputs
n_obs = n_hours * n_features
train_X, train_y = train[:, :n_obs], train[:, -n_features]
test_X, test_y = test[:, :n_obs], test[:, -n_features]
print(train_X.shape, len(train_X), train_y.shape)
# reshape input to be 3D [samples, timesteps, features]
train_X = train_X.reshape((train_X.shape[0], n_hours, n_features))
test_X = test_X.reshape((test_X.shape[0], n_hours, n_features))
print(train_X.shape, train_y.shape, test_X.shape, test_y.shape)

(400, 18) 400 (400,)
(400, 2, 9) (400,) (135, 2, 9) (135,)


In [18]:
reframed

var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2     0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3     0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4     0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5     0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6     0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   
..         ...        ...        ...        ...        ...        ...   
532   0.647471   0.350071   0.683410   0.600138   0.604167   0.304962   
533   0.624708   0.579207   0.717050   0.770611   0.531250   0.351837   
534   0.797471   0.478075   0.801382   0.687265   0.781250   0.186211   
535   0.766732   0.534690   0.864055   0.749342   0.687500   0.286762   
536   0.690856   0.608430   0.800000   0.597099   0.791667   0.308640   

     var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  ...  var9(t-1)   var1(t)  \
2     0.001171   0.706132   0.735252   0.055642  ...   0.697631  0.075875   
3     0.000861   0.674529   0.697631   0.075875  ...   0.797491  0.103307   
4     0.000861   0.823113   0.797491   0.103307  ...   0.810961  0.176265   
5     0.003931   0.802359   0.810961   0.176265  ...   0.823037  0.143191   
6     0.001171   0.840095   0.823037   0.143191  ...   0.573618  0.144163   
..         ...        ...        ...        ...  ...        ...       ...   
532   0.015390   0.658019   0.671620   0.624708  ...   0.698095  0.797471   
533   0.000002   0.708019   0.698095   0.797471  ...   0.819786  0.766732   
534   0.075827   0.788679   0.819786   0.766732  ...   0.856014  0.690856   
535   0.000002   0.866982   0.856014   0.690856  ...   0.820714  0.663813   
536   0.090269   0.780190   0.820714   0.663813  ...   0.826753  0.792801   

      var2(t)   var3(t)   var4(t)   var5(t)   var6(t)   var7(t)   var8(t)  \
2    0.675534  0.822119  0.834066  0.541667  0.329227  0.000861  0.823113   
3    0.721197  0.808756  0.800696  0.677083  0.259926  0.003931  0.802359   
4    0.554569  0.833639  0.748459  0.697917  0.157902  0.001171  0.840095   
5    0.288067  0.575576  0.597859  0.500000  0.110291  0.190853  0.546227   
6    0.366840  0.649308  0.503348  0.656250  0.150917  0.132394  0.598114   
..        ...       ...       ...       ...       ...       ...       ...   
532  0.478075  0.801382  0.687265  0.781250  0.186211  0.075827  0.788679   
533  0.534690  0.864055  0.749342  0.687500  0.286762  0.000002  0.866982   
534  0.608430  0.800000  0.597099  0.791667  0.308640  0.090269  0.780190   
535  0.418575  0.819816  0.612433  0.729167  0.255695  0.000616  0.825472   
536  0.317628  0.627189  0.454131  0.572917  0.294670  0.002762  0.609907   

      var9(t)  
2    0.797491  
3    0.810961  
4    0.823037  
5    0.573618  
6    0.680910  
..        ...  
532  0.819786  
533  0.856014  
534  0.820714  
535  0.826753  
536  0.631677  

[535 rows x 27 columns]

In [19]:
# drop columns we don't want to predict
#reframed.drop(reframed.columns[[55,56,57,58,59,60,61,62]], axis=1, inplace=True)
#reframed.drop(reframed.columns[[109,110,111,112,113,114,115,116]], axis=1, inplace=True)
reframed.drop(reframed.columns[[19,20,21,22,23,24,25,26]], axis=1, inplace=True)
print(reframed.head())

   var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2   0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3   0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4   0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5   0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6   0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   

   var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  var2(t-1)  var3(t-1)  \
2   0.001171   0.706132   0.735252   0.055642   0.368665   0.694469   
3   0.000861   0.674529   0.697631   0.075875   0.675534   0.822119   
4   0.000861   0.823113   0.797491   0.103307   0.721197   0.808756   
5   0.003931   0.802359   0.810961   0.176265   0.554569   0.833639   
6   0.001171   0.840095   0.823037   0.143191   0.288067   0.575576   

   var4(t-1)  var5(t-1)  var6(t-1)  var7(t-1)  var8(t-1)  var9(t-1)   var1(t)  
2   0.660572   0.468750   0.265625   0.000861   0.674529   0.69763

In [20]:
# create model
model = KerasRegressor(build_fn=create_model,epochs=100, batch_size=18, verbose=1)

In [21]:
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=3)
#grid_result = grid.fit(train_X, train_y)

from sklearn.model_selection import TimeSeriesSplit
tscv = TimeSeriesSplit(n_splits=3).get_n_splits([train_X, train_y])
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_absolute_error')
grid_result = grid.fit(train_X, train_y)

Train on 266 samples
Epoch 1/100
266/266 [==============================] - 9s 35ms/sample - loss: 0.1641
Epoch 2/100
266/266 [==============================] - 0s 704us/sample - loss: 0.1244
Epoch 3/100
266/266 [==============================] - 0s 673us/sample - loss: 0.1229
Epoch 4/100
266/266 [==============================] - 0s 701us/sample - loss: 0.1223
Epoch 5/100
266/266 [==============================] - 0s 711us/sample - loss: 0.1209
Epoch 6/100
266/266 [==============================] - 0s 686us/sample - loss: 0.1198
Epoch 7/100
266/266 [==============================] - 0s 686us/sample - loss: 0.1187
Epoch 8/100
266/266 [==============================] - 0s 710us/sample - loss: 0.1175
Epoch 9/100
266/266 [==============================] - 0s 756us/sample - loss: 0.1165
Epoch 10/100
266/266 [==============================] - 0s 714us/sample - loss: 0.1159
Epoch 11/100
266/266 [==============================] - 0s 727us/sample - loss: 0.1145
Epoch 12/100
266/266 [==========

267/267 [==============================] - 0s 688us/sample - loss: 0.1077
Epoch 88/100
267/267 [==============================] - 0s 717us/sample - loss: 0.1073
Epoch 89/100
267/267 [==============================] - 0s 665us/sample - loss: 0.1064
Epoch 90/100
267/267 [==============================] - 0s 673us/sample - loss: 0.1062
Epoch 91/100
267/267 [==============================] - 0s 689us/sample - loss: 0.1054
Epoch 92/100
267/267 [==============================] - 0s 704us/sample - loss: 0.1036
Epoch 93/100
267/267 [==============================] - 0s 718us/sample - loss: 0.1038
Epoch 94/100
267/267 [==============================] - 0s 661us/sample - loss: 0.1015
Epoch 95/100
267/267 [==============================] - 0s 688us/sample - loss: 0.1018
Epoch 96/100
267/267 [==============================] - 0s 702us/sample - loss: 0.1010
Epoch 97/100
267/267 [==============================] - 0s 720us/sample - loss: 0.0997
Epoch 98/100
267/267 [==============================] - 

266/266 [==============================] - 0s 736us/sample - loss: 0.0396
Epoch 74/100
266/266 [==============================] - 0s 743us/sample - loss: 0.0385
Epoch 75/100
266/266 [==============================] - 0s 730us/sample - loss: 0.0396
Epoch 76/100
266/266 [==============================] - 0s 751us/sample - loss: 0.0400
Epoch 77/100
266/266 [==============================] - 0s 748us/sample - loss: 0.0396
Epoch 78/100
266/266 [==============================] - 0s 736us/sample - loss: 0.0381
Epoch 79/100
266/266 [==============================] - 0s 741us/sample - loss: 0.0392
Epoch 80/100
266/266 [==============================] - 0s 746us/sample - loss: 0.0378
Epoch 81/100
266/266 [==============================] - 0s 752us/sample - loss: 0.0382
Epoch 82/100
266/266 [==============================] - 0s 763us/sample - loss: 0.0390
Epoch 83/100
266/266 [==============================] - 0s 750us/sample - loss: 0.0412
Epoch 84/100
266/266 [==============================] - 

267/267 [==============================] - 0s 758us/sample - loss: 0.0312
Epoch 59/100
267/267 [==============================] - 0s 747us/sample - loss: 0.0328
Epoch 60/100
267/267 [==============================] - 0s 760us/sample - loss: 0.0311
Epoch 61/100
267/267 [==============================] - 0s 758us/sample - loss: 0.0317
Epoch 62/100
267/267 [==============================] - 0s 742us/sample - loss: 0.0296
Epoch 63/100
267/267 [==============================] - 0s 762us/sample - loss: 0.0322
Epoch 64/100
267/267 [==============================] - 0s 755us/sample - loss: 0.0302
Epoch 65/100
267/267 [==============================] - 0s 745us/sample - loss: 0.0284
Epoch 66/100
267/267 [==============================] - 0s 747us/sample - loss: 0.0296
Epoch 67/100
267/267 [==============================] - 0s 751us/sample - loss: 0.0310
Epoch 68/100
267/267 [==============================] - 0s 755us/sample - loss: 0.0295
Epoch 69/100
267/267 [==============================] - 

267/267 [==============================] - 0s 1ms/sample - loss: 0.0541
Epoch 45/100
267/267 [==============================] - 0s 1ms/sample - loss: 0.0535
Epoch 46/100
267/267 [==============================] - 0s 807us/sample - loss: 0.0527
Epoch 47/100
267/267 [==============================] - 0s 725us/sample - loss: 0.0519
Epoch 48/100
267/267 [==============================] - 0s 688us/sample - loss: 0.0514
Epoch 49/100
267/267 [==============================] - 0s 657us/sample - loss: 0.0507
Epoch 50/100
267/267 [==============================] - 0s 797us/sample - loss: 0.0501
Epoch 51/100
267/267 [==============================] - 0s 691us/sample - loss: 0.0496
Epoch 52/100
267/267 [==============================] - 0s 743us/sample - loss: 0.0492
Epoch 53/100
267/267 [==============================] - 0s 791us/sample - loss: 0.0488
Epoch 54/100
267/267 [==============================] - 0s 705us/sample - loss: 0.0486
Epoch 55/100
267/267 [==============================] - 0s 7

...

267/267 [==============================] - 0s 735us/sample - loss: 0.1351
Epoch 3/100
267/267 [==============================] - 0s 700us/sample - loss: 0.1204
Epoch 4/100
267/267 [==============================] - 0s 705us/sample - loss: 0.0999
Epoch 5/100
267/267 [==============================] - 0s 693us/sample - loss: 0.0652
Epoch 6/100
267/267 [==============================] - 0s 705us/sample - loss: 0.0504
Epoch 7/100
267/267 [==============================] - 0s 711us/sample - loss: 0.0449
Epoch 8/100
267/267 [==============================] - 0s 716us/sample - loss: 0.0464
Epoch 9/100
267/267 [==============================] - 0s 696us/sample - loss: 0.0459
Epoch 10/100
267/267 [==============================] - 0s 721us/sample - loss: 0.0410
Epoch 11/100
267/267 [==============================] - 0s 718us/sample - loss: 0.0430
Epoch 12/100
267/267 [==============================] - 0s 726us/sample - loss: 0.0423
Epoch 13/100
267/267 [==============================] - 0s 724u

267/267 [==============================] - 0s 716us/sample - loss: 0.0250
Epoch 90/100
267/267 [==============================] - 0s 697us/sample - loss: 0.0253
Epoch 91/100
267/267 [==============================] - 0s 716us/sample - loss: 0.0247
Epoch 92/100
267/267 [==============================] - 0s 699us/sample - loss: 0.0253
Epoch 93/100
267/267 [==============================] - 0s 694us/sample - loss: 0.0243
Epoch 94/100
267/267 [==============================] - 0s 716us/sample - loss: 0.0247
Epoch 95/100
267/267 [==============================] - 0s 714us/sample - loss: 0.0250
Epoch 96/100
267/267 [==============================] - 0s 713us/sample - loss: 0.0246
Epoch 97/100
267/267 [==============================] - 0s 692us/sample - loss: 0.0244
Epoch 98/100
267/267 [==============================] - 0s 703us/sample - loss: 0.0260
Epoch 99/100
267/267 [==============================] - 0s 691us/sample - loss: 0.0261
Epoch 100/100
133/133 [==============================] -

267/267 [==============================] - 0s 742us/sample - loss: 0.0397
Epoch 76/100
267/267 [==============================] - 0s 737us/sample - loss: 0.0390
Epoch 77/100
267/267 [==============================] - 0s 756us/sample - loss: 0.0379
Epoch 78/100
267/267 [==============================] - 0s 728us/sample - loss: 0.0386
Epoch 79/100
267/267 [==============================] - 0s 731us/sample - loss: 0.0391
Epoch 80/100
267/267 [==============================] - 0s 758us/sample - loss: 0.0401
Epoch 81/100
267/267 [==============================] - 0s 734us/sample - loss: 0.0397
Epoch 82/100
267/267 [==============================] - 0s 718us/sample - loss: 0.0394
Epoch 83/100
267/267 [==============================] - 0s 746us/sample - loss: 0.0381
Epoch 84/100
267/267 [==============================] - 0s 728us/sample - loss: 0.0385
Epoch 85/100
267/267 [==============================] - 0s 715us/sample - loss: 0.0385
Epoch 86/100
267/267 [==============================] - 

266/266 [==============================] - 0s 862us/sample - loss: 0.0421
Epoch 62/100
266/266 [==============================] - 0s 828us/sample - loss: 0.0394
Epoch 63/100
266/266 [==============================] - 0s 831us/sample - loss: 0.0376
Epoch 64/100
266/266 [==============================] - 0s 815us/sample - loss: 0.0374
Epoch 65/100
266/266 [==============================] - 0s 839us/sample - loss: 0.0367
Epoch 66/100
266/266 [==============================] - 0s 835us/sample - loss: 0.0381
Epoch 67/100
266/266 [==============================] - 0s 839us/sample - loss: 0.0375
Epoch 68/100
266/266 [==============================] - 0s 842us/sample - loss: 0.0362
Epoch 69/100
266/266 [==============================] - 0s 846us/sample - loss: 0.0389
Epoch 70/100
266/266 [==============================] - 0s 834us/sample - loss: 0.0380
Epoch 71/100
266/266 [==============================] - 0s 854us/sample - loss: 0.0370
Epoch 72/100
266/266 [==============================] - 

267/267 [==============================] - 0s 823us/sample - loss: 0.0312
Epoch 48/100
267/267 [==============================] - 0s 839us/sample - loss: 0.0308
Epoch 49/100
267/267 [==============================] - 0s 843us/sample - loss: 0.0291
Epoch 50/100
267/267 [==============================] - 0s 830us/sample - loss: 0.0303
Epoch 51/100
267/267 [==============================] - 0s 821us/sample - loss: 0.0296
Epoch 52/100
267/267 [==============================] - 0s 839us/sample - loss: 0.0328
Epoch 53/100
267/267 [==============================] - 0s 818us/sample - loss: 0.0315
Epoch 54/100
267/267 [==============================] - 0s 832us/sample - loss: 0.0294
Epoch 55/100
267/267 [==============================] - 0s 822us/sample - loss: 0.0280
Epoch 56/100
267/267 [==============================] - 0s 820us/sample - loss: 0.0309
Epoch 57/100
267/267 [==============================] - 0s 829us/sample - loss: 0.0277
Epoch 58/100
267/267 [==============================] - 

In [22]:
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Best: -0.037071 using {'optimizer': 'Adam'}
-0.151178 (0.072287) with: {'optimizer': 'SGD'}
-0.056283 (0.017031) with: {'optimizer': 'RMSprop'}
-0.075437 (0.034355) with: {'optimizer': 'Adagrad'}
-0.189916 (0.116425) with: {'optimizer': 'Adadelta'}
-0.037071 (0.005971) with: {'optimizer': 'Adam'}
-0.043874 (0.006565) with: {'optimizer': 'Adamax'}
-0.041722 (0.008999) with: {'optimizer': 'Nadam'}


In [32]:
import os
####*IMPORANT*: Have to do this line *before* importing tensorflow
os.environ['PYTHONHASHSEED']=str(1)
import numpy as np
import tensorflow as tf
from tensorflow import keras
import random

# Use scikit-learn to grid search the batch size and epochs
import numpy
from sklearn.model_selection import GridSearchCV
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.wrappers.scikit_learn import KerasRegressor

# Function to create model, required for KerasClassifier
from math import sqrt
from numpy import concatenate
from matplotlib import pyplot
from pandas import read_csv
from pandas import DataFrame
from pandas import concat
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_squared_error
from tensorflow.keras.layers import LSTM
import keras
from tensorflow.keras.optimizers import Adam

def reset_random_seeds():
   os.environ['PYTHONHASHSEED']=str(1)
   tf.random.set_seed(1)
   np.random.seed(1)
   random.seed(1)

#make some random data
reset_random_seeds()
#np.random.rand(4)


# design network for tuning learning rate and momentum
#def create_model(learn_rate=0.01):
#    model = Sequential()
 #   model.add(LSTM(50, input_shape=(train_X.shape[1], train_X.shape[2])))
  #  model.add(Dense(1))
   # #compile model
    #optimizer = Adam(lr=learn_rate)
    #model.compile(loss='mse', optimizer=optimizer, metrics=['mse']) # can be mse or mae
    #return model


# design network
def create_model(learn_rate=0.01):
    model = Sequential()
    model.add(LSTM(50, return_sequences=True, input_shape=(train_X.shape[1], train_X.shape[2])))
    model.add(LSTM(50))
    model.add(Dense(10))
    model.add(Dense(1))
    #mse or mae it got better with mae
    optimizer = Adam(lr=learn_rate)
    model.compile(loss='mae', optimizer=optimizer, metrics=['mae']) # can be mse or mae
    return model

In [33]:
#define the grid search parameters    
learn_rate = [0.0001, 0.001, 0.01, 0.1, 0.2, 0.3]
#momentum = [0.0, 0.2, 0.4, 0.6, 0.8, 0.9]

param_grid = dict(learn_rate=learn_rate)


In [34]:
# fix random seed for reproducibility
seed = 1 #seed 7
numpy.random.seed(seed)
#numpy.random.rand(4)

# convert series to supervised learning
def series_to_supervised(data, n_in=1, n_out=1, dropnan=True):
    n_vars = 1 if type(data) is list else data.shape[1]
    df = DataFrame(data)
    cols, names = list(), list()
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
        cols.append(df.shift(i))
        names += [('var%d(t-%d)' % (j+1, i)) for j in range(n_vars)]
    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df.shift(-i))
        if i == 0:
            names += [('var%d(t)' % (j+1)) for j in range(n_vars)]
        else:
            names += [('var%d(t+%d)' % (j+1, i)) for j in range(n_vars)]
    # put it all together
    agg = concat(cols, axis=1)
    agg.columns = names
    # drop rows with NaN values
    if dropnan:
        agg.dropna(inplace=True)
    return agg

In [35]:
# load dataset
dataset = read_csv('C:/Users/*', header=0, index_col=0)
values = dataset.values

# ensure all data is float
values = values.astype('float32')

# normalize features
scaler = MinMaxScaler(feature_range=(0, 1))
scaled = scaler.fit_transform(values)

# specify the number of lag hours
n_hours = 2
n_features = 9

# frame as supervised learning
reframed = series_to_supervised(scaled, n_hours, 1)
print(reframed.shape)

reframed

(535, 27)


var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2     0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3     0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4     0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5     0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6     0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   
..         ...        ...        ...        ...        ...        ...   
532   0.647471   0.350071   0.683410   0.600138   0.604167   0.304962   
533   0.624708   0.579207   0.717050   0.770611   0.531250   0.351837   
534   0.797471   0.478075   0.801382   0.687265   0.781250   0.186211   
535   0.766732   0.534690   0.864055   0.749342   0.687500   0.286762   
536   0.690856   0.608430   0.800000   0.597099   0.791667   0.308640   

     var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  ...  var9(t-1)   var1(t)  \
2     0.001171   0.706132   0.735252   0.055642  ...   0.697631  0.075875   
3     0.000861   0.674529   0.697631   0.075875  ...   0.797491  0.103307   
4     0.000861   0.823113   0.797491   0.103307  ...   0.810961  0.176265   
5     0.003931   0.802359   0.810961   0.176265  ...   0.823037  0.143191   
6     0.001171   0.840095   0.823037   0.143191  ...   0.573618  0.144163   
..         ...        ...        ...        ...  ...        ...       ...   
532   0.015390   0.658019   0.671620   0.624708  ...   0.698095  0.797471   
533   0.000002   0.708019   0.698095   0.797471  ...   0.819786  0.766732   
534   0.075827   0.788679   0.819786   0.766732  ...   0.856014  0.690856   
535   0.000002   0.866982   0.856014   0.690856  ...   0.820714  0.663813   
536   0.090269   0.780190   0.820714   0.663813  ...   0.826753  0.792801   

      var2(t)   var3(t)   var4(t)   var5(t)   var6(t)   var7(t)   var8(t)  \
2    0.675534  0.822119  0.834066  0.541667  0.329227  0.000861  0.823113   
3    0.721197  0.808756  0.800696  0.677083  0.259926  0.003931  0.802359   
4    0.554569  0.833639  0.748459  0.697917  0.157902  0.001171  0.840095   
5    0.288067  0.575576  0.597859  0.500000  0.110291  0.190853  0.546227   
6    0.366840  0.649308  0.503348  0.656250  0.150917  0.132394  0.598114   
..        ...       ...       ...       ...       ...       ...       ...   
532  0.478075  0.801382  0.687265  0.781250  0.186211  0.075827  0.788679   
533  0.534690  0.864055  0.749342  0.687500  0.286762  0.000002  0.866982   
534  0.608430  0.800000  0.597099  0.791667  0.308640  0.090269  0.780190   
535  0.418575  0.819816  0.612433  0.729167  0.255695  0.000616  0.825472   
536  0.317628  0.627189  0.454131  0.572917  0.294670  0.002762  0.609907   

      var9(t)  
2    0.797491  
3    0.810961  
4    0.823037  
5    0.573618  
6    0.680910  
..        ...  
532  0.819786  
533  0.856014  
534  0.820714  
535  0.826753  
536  0.631677  

[535 rows x 27 columns]

In [36]:
# split into train and test sets
values = reframed.values
n_train_hours = 400
train = values[:n_train_hours, :]
test = values[n_train_hours:, :]
# split into input and outputs
n_obs = n_hours * n_features
train_X, train_y = train[:, :n_obs], train[:, -n_features]
test_X, test_y = test[:, :n_obs], test[:, -n_features]
print(train_X.shape, len(train_X), train_y.shape)
# reshape input to be 3D [samples, timesteps, features]
train_X = train_X.reshape((train_X.shape[0], n_hours, n_features))
test_X = test_X.reshape((test_X.shape[0], n_hours, n_features))
print(train_X.shape, train_y.shape, test_X.shape, test_y.shape)

(400, 18) 400 (400,)
(400, 2, 9) (400,) (135, 2, 9) (135,)


In [37]:
# drop columns we don't want to predict
#reframed.drop(reframed.columns[[55,56,57,58,59,60,61,62]], axis=1, inplace=True)
#reframed.drop(reframed.columns[[109,110,111,112,113,114,115,116]], axis=1, inplace=True)
reframed.drop(reframed.columns[[19,20,21,22,23,24,25,26]], axis=1, inplace=True)
print(reframed.head())

   var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2   0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3   0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4   0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5   0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6   0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   

   var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  var2(t-1)  var3(t-1)  \
2   0.001171   0.706132   0.735252   0.055642   0.368665   0.694469   
3   0.000861   0.674529   0.697631   0.075875   0.675534   0.822119   
4   0.000861   0.823113   0.797491   0.103307   0.721197   0.808756   
5   0.003931   0.802359   0.810961   0.176265   0.554569   0.833639   
6   0.001171   0.840095   0.823037   0.143191   0.288067   0.575576   

   var4(t-1)  var5(t-1)  var6(t-1)  var7(t-1)  var8(t-1)  var9(t-1)   var1(t)  
2   0.660572   0.468750   0.265625   0.000861   0.674529   0.69763

In [38]:
# create model
model = KerasRegressor(build_fn=create_model,epochs=100, batch_size=18, verbose=1)

In [39]:
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=3)
#grid_result = grid.fit(train_X, train_y)

from sklearn.model_selection import TimeSeriesSplit
tscv = TimeSeriesSplit(n_splits=3).get_n_splits([train_X, train_y])
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_absolute_error')
grid_result = grid.fit(train_X, train_y)

#from sklearn.model_selection import TimeSeriesSplit
#tscv = TimeSeriesSplit(n_splits=3)
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_squared_error')
#grid_result = grid.fit(train_X, train_y)

Train on 266 samples
Epoch 1/100
266/266 [==============================] - 7s 26ms/sample - loss: 0.2762 - mae: 0.2762
Epoch 2/100
266/266 [==============================] - 0s 733us/sample - loss: 0.2383 - mae: 0.2383
Epoch 3/100
266/266 [==============================] - 0s 758us/sample - loss: 0.1992 - mae: 0.1992
Epoch 4/100
266/266 [==============================] - 0s 746us/sample - loss: 0.1607 - mae: 0.1607
Epoch 5/100
266/266 [==============================] - 0s 750us/sample - loss: 0.1250 - mae: 0.1250
Epoch 6/100
266/266 [==============================] - 0s 767us/sample - loss: 0.1014 - mae: 0.1014
Epoch 7/100
266/266 [==============================] - 0s 778us/sample - loss: 0.0927 - mae: 0.0927
Epoch 8/100
266/266 [==============================] - 0s 782us/sample - loss: 0.0894 - mae: 0.0894
Epoch 9/100
266/266 [==============================] - 0s 780us/sample - loss: 0.0871 - mae: 0.0871
Epoch 10/100
266/266 [==============================] - 0s 737us/sample - loss: 

266/266 [==============================] - 0s 758us/sample - loss: 0.0477 - mae: 0.0477
Epoch 83/100
266/266 [==============================] - 0s 756us/sample - loss: 0.0480 - mae: 0.0480
Epoch 84/100
266/266 [==============================] - 0s 767us/sample - loss: 0.0475 - mae: 0.0475
Epoch 85/100
266/266 [==============================] - 0s 752us/sample - loss: 0.0472 - mae: 0.0472
Epoch 86/100
266/266 [==============================] - 0s 780us/sample - loss: 0.0472 - mae: 0.0472
Epoch 87/100
266/266 [==============================] - 0s 751us/sample - loss: 0.0474 - mae: 0.0474
Epoch 88/100
266/266 [==============================] - 0s 754us/sample - loss: 0.0472 - mae: 0.0472
Epoch 89/100
266/266 [==============================] - 0s 750us/sample - loss: 0.0469 - mae: 0.0469
Epoch 90/100
266/266 [==============================] - 0s 775us/sample - loss: 0.0467 - mae: 0.0467
Epoch 91/100
266/266 [==============================] - 0s 749us/sample - loss: 0.0465 - mae: 0.0465
Epo

267/267 [==============================] - 0s 761us/sample - loss: 0.0506 - mae: 0.0506
Epoch 43/100
267/267 [==============================] - 0s 758us/sample - loss: 0.0483 - mae: 0.0483
Epoch 44/100
267/267 [==============================] - 0s 755us/sample - loss: 0.0466 - mae: 0.0466
Epoch 45/100
267/267 [==============================] - 0s 755us/sample - loss: 0.0457 - mae: 0.0457
Epoch 46/100
267/267 [==============================] - 0s 746us/sample - loss: 0.0430 - mae: 0.0430
Epoch 47/100
267/267 [==============================] - 0s 762us/sample - loss: 0.0421 - mae: 0.0421
Epoch 48/100
267/267 [==============================] - 0s 747us/sample - loss: 0.0398 - mae: 0.0398
Epoch 49/100
267/267 [==============================] - 0s 747us/sample - loss: 0.0390 - mae: 0.0390
Epoch 50/100
267/267 [==============================] - 0s 754us/sample - loss: 0.0380 - mae: 0.0380
Epoch 51/100
267/267 [==============================] - 0s 748us/sample - loss: 0.0372 - mae: 0.0372
Epo

267/267 [==============================] - 0s 741us/sample - loss: 0.1226 - mae: 0.1226
Epoch 3/100
267/267 [==============================] - 0s 763us/sample - loss: 0.1046 - mae: 0.1046
Epoch 4/100
267/267 [==============================] - 0s 764us/sample - loss: 0.0758 - mae: 0.0758
Epoch 5/100
267/267 [==============================] - 0s 772us/sample - loss: 0.0512 - mae: 0.0512
Epoch 6/100
267/267 [==============================] - 0s 761us/sample - loss: 0.0470 - mae: 0.0470
Epoch 7/100
267/267 [==============================] - 0s 781us/sample - loss: 0.0448 - mae: 0.0448
Epoch 8/100
267/267 [==============================] - 0s 798us/sample - loss: 0.0455 - mae: 0.0455
Epoch 9/100
267/267 [==============================] - 0s 788us/sample - loss: 0.0455 - mae: 0.0455
Epoch 10/100
267/267 [==============================] - 0s 769us/sample - loss: 0.0411 - mae: 0.0411
Epoch 11/100
267/267 [==============================] - 0s 735us/sample - loss: 0.0437 - mae: 0.0437
Epoch 12/1

267/267 [==============================] - 0s 758us/sample - loss: 0.0278 - mae: 0.0278
Epoch 63/100
267/267 [==============================] - 0s 754us/sample - loss: 0.0269 - mae: 0.0269
Epoch 64/100
267/267 [==============================] - 0s 739us/sample - loss: 0.0254 - mae: 0.0254
Epoch 65/100
267/267 [==============================] - 0s 704us/sample - loss: 0.0257 - mae: 0.0257
Epoch 66/100
267/267 [==============================] - 0s 749us/sample - loss: 0.0274 - mae: 0.0274
Epoch 67/100
267/267 [==============================] - 0s 751us/sample - loss: 0.0270 - mae: 0.0270
Epoch 68/100
267/267 [==============================] - 0s 728us/sample - loss: 0.0256 - mae: 0.0256
Epoch 69/100
267/267 [==============================] - 0s 759us/sample - loss: 0.0262 - mae: 0.0262
Epoch 70/100
267/267 [==============================] - 0s 742us/sample - loss: 0.0273 - mae: 0.0273
Epoch 71/100
267/267 [==============================] - 0s 739us/sample - loss: 0.0290 - mae: 0.0290
Epo

...

266/266 [==============================] - 0s 818us/sample - loss: 0.2593 - mae: 0.2593
Epoch 4/100
266/266 [==============================] - 0s 801us/sample - loss: 0.1331 - mae: 0.1331
Epoch 5/100
266/266 [==============================] - 0s 747us/sample - loss: 0.1317 - mae: 0.1317
Epoch 6/100
266/266 [==============================] - 0s 804us/sample - loss: 0.1352 - mae: 0.1352
Epoch 7/100
266/266 [==============================] - 0s 825us/sample - loss: 0.1279 - mae: 0.1279
Epoch 8/100
266/266 [==============================] - 0s 812us/sample - loss: 0.1270 - mae: 0.1270
Epoch 9/100
266/266 [==============================] - 0s 828us/sample - loss: 0.1301 - mae: 0.1301
Epoch 10/100
266/266 [==============================] - 0s 848us/sample - loss: 0.1276 - mae: 0.1276
Epoch 11/100
266/266 [==============================] - 0s 796us/sample - loss: 0.1360 - mae: 0.1360
Epoch 12/100
266/266 [==============================] - 0s 731us/sample - loss: 0.1284 - mae: 0.1284
Epoch 13/

267/267 [==============================] - 0s 736us/sample - loss: 0.1518 - mae: 0.1518
Epoch 65/100
267/267 [==============================] - 0s 747us/sample - loss: 0.1483 - mae: 0.1483
Epoch 66/100
267/267 [==============================] - 0s 740us/sample - loss: 0.1561 - mae: 0.1561
Epoch 67/100
267/267 [==============================] - 0s 728us/sample - loss: 0.1510 - mae: 0.1510
Epoch 68/100
267/267 [==============================] - 0s 743us/sample - loss: 0.1552 - mae: 0.1552
Epoch 69/100
267/267 [==============================] - 0s 738us/sample - loss: 0.1466 - mae: 0.1466
Epoch 70/100
267/267 [==============================] - 0s 699us/sample - loss: 0.1464 - mae: 0.1464
Epoch 71/100
267/267 [==============================] - 0s 728us/sample - loss: 0.1534 - mae: 0.1534
Epoch 72/100
267/267 [==============================] - 0s 698us/sample - loss: 0.1498 - mae: 0.1498
Epoch 73/100
267/267 [==============================] - 0s 733us/sample - loss: 0.1498 - mae: 0.1498
Epo

266/266 [==============================] - 0s 352us/sample - loss: 0.1783 - mae: 0.1783
Epoch 24/100
266/266 [==============================] - 0s 294us/sample - loss: 0.4070 - mae: 0.4070
Epoch 25/100
266/266 [==============================] - 0s 294us/sample - loss: 1.3246 - mae: 1.3246
Epoch 26/100
266/266 [==============================] - 0s 294us/sample - loss: 2.8249 - mae: 2.8249
Epoch 27/100
266/266 [==============================] - 0s 294us/sample - loss: 1.5079 - mae: 1.5079
Epoch 28/100
266/266 [==============================] - 0s 352us/sample - loss: 1.4988 - mae: 1.4988
Epoch 29/100
266/266 [==============================] - 0s 294us/sample - loss: 0.5209 - mae: 0.5209
Epoch 30/100
266/266 [==============================] - 0s 294us/sample - loss: 0.2805 - mae: 0.2805
Epoch 31/100
266/266 [==============================] - 0s 321us/sample - loss: 0.2340 - mae: 0.2340
Epoch 32/100
266/266 [==============================] - 0s 315us/sample - loss: 0.1691 - mae: 0.1691
Epo

267/267 [==============================] - 0s 321us/sample - loss: 0.1450 - mae: 0.1450
Epoch 85/100
267/267 [==============================] - 0s 288us/sample - loss: 0.1448 - mae: 0.1448
Epoch 86/100
267/267 [==============================] - 0s 317us/sample - loss: 0.1496 - mae: 0.1496
Epoch 87/100
267/267 [==============================] - 0s 317us/sample - loss: 0.1445 - mae: 0.1445
Epoch 88/100
267/267 [==============================] - 0s 375us/sample - loss: 0.1447 - mae: 0.1447
Epoch 89/100
267/267 [==============================] - 0s 293us/sample - loss: 0.1562 - mae: 0.1562
Epoch 90/100
267/267 [==============================] - 0s 317us/sample - loss: 0.1598 - mae: 0.1598
Epoch 91/100
267/267 [==============================] - 0s 317us/sample - loss: 0.1917 - mae: 0.1917
Epoch 92/100
267/267 [==============================] - 0s 317us/sample - loss: 0.3886 - mae: 0.3886
Epoch 93/100
267/267 [==============================] - 0s 317us/sample - loss: 0.3955 - mae: 0.3955
Epo

400/400 [==============================] - 0s 312us/sample - loss: 0.0348 - mae: 0.0348
Epoch 45/100
400/400 [==============================] - 0s 391us/sample - loss: 0.0327 - mae: 0.0327
Epoch 46/100
400/400 [==============================] - 0s 436us/sample - loss: 0.0325 - mae: 0.0325
Epoch 47/100
400/400 [==============================] - 0s 384us/sample - loss: 0.0339 - mae: 0.0339
Epoch 48/100
400/400 [==============================] - 0s 391us/sample - loss: 0.0340 - mae: 0.0340
Epoch 49/100
400/400 [==============================] - 0s 351us/sample - loss: 0.0336 - mae: 0.0336
Epoch 50/100
400/400 [==============================] - 0s 430us/sample - loss: 0.0334 - mae: 0.0334
Epoch 51/100
400/400 [==============================] - 0s 402us/sample - loss: 0.0319 - mae: 0.0319
Epoch 52/100
400/400 [==============================] - 0s 357us/sample - loss: 0.0323 - mae: 0.0323
Epoch 53/100
400/400 [==============================] - 0s 342us/sample - loss: 0.0368 - mae: 0.0368
Epo

In [40]:
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Best: -0.039321 using {'learn_rate': 0.001}
-0.057111 (0.014923) with: {'learn_rate': 0.0001}
-0.039321 (0.008177) with: {'learn_rate': 0.001}
-0.054957 (0.015060) with: {'learn_rate': 0.01}
-0.062453 (0.021294) with: {'learn_rate': 0.1}
-0.180398 (0.061781) with: {'learn_rate': 0.2}
-0.121110 (0.046214) with: {'learn_rate': 0.3}


In [50]:
import os
####*IMPORANT*: Have to do this line *before* importing tensorflow
os.environ['PYTHONHASHSEED']=str(1)
import numpy as np
import tensorflow as tf
from tensorflow import keras
import random

# Use scikit-learn to grid search the batch size and epochs
import numpy
from sklearn.model_selection import GridSearchCV
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.wrappers.scikit_learn import KerasRegressor

# Function to create model, required for KerasClassifier
from math import sqrt
from numpy import concatenate
from matplotlib import pyplot
from pandas import read_csv
from pandas import DataFrame
from pandas import concat
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_squared_error
from tensorflow.keras.layers import LSTM
import keras
from tensorflow.keras.optimizers import Adam
from tensorflow.keras import initializers

def reset_random_seeds():
   os.environ['PYTHONHASHSEED']=str(1)
   tf.random.set_seed(1)
   np.random.seed(1)
   random.seed(1)

#make some random data
reset_random_seeds()
#np.random.rand(4)

# design network for tuning kernel intializer
#def create_model(kernel_initializer='uniform'):
 #   model = Sequential()
 #   model.add(LSTM(50, kernel_initializer=kernel_initializer,input_shape=(train_X.shape[1], train_X.shape[2])))
  #  model.add(Dense(1, kernel_initializer=kernel_initializer))
   # #compile model
   # model.compile(loss='mae', optimizer='adam', metrics=['mae']) # can be mse or mae
    #return model

# design network
def create_model(kernel_initializer='uniform'):
    model = Sequential()
    model.add(LSTM(50,kernel_initializer=kernel_initializer, return_sequences=True, input_shape=(train_X.shape[1], train_X.shape[2])))
    model.add(LSTM(50,kernel_initializer=kernel_initializer))
    model.add(Dense(10,kernel_initializer=kernel_initializer))
    model.add(Dense(1,kernel_initializer=kernel_initializer))
    #mse or mae it got better with mae
    model.compile(loss='mae', optimizer='adam', metrics=['mae']) # can be mse or mae
    return model

In [51]:
kernel_initializer = ['uniform', 'random_normal','random_uniform', 'truncated_normal','ones','identity','lecun_uniform', 'normal', 'zeros', 'glorot_normal', 'glorot_uniform', 'he_normal', 'he_uniform']

param_grid = dict(kernel_initializer=kernel_initializer)

In [52]:
# fix random seed for reproducibility
seed = 1 #seed 7
numpy.random.seed(seed)
#numpy.random.rand(4)

# convert series to supervised learning
def series_to_supervised(data, n_in=1, n_out=1, dropnan=True):
    n_vars = 1 if type(data) is list else data.shape[1]
    df = DataFrame(data)
    cols, names = list(), list()
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
        cols.append(df.shift(i))
        names += [('var%d(t-%d)' % (j+1, i)) for j in range(n_vars)]
    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df.shift(-i))
        if i == 0:
            names += [('var%d(t)' % (j+1)) for j in range(n_vars)]
        else:
            names += [('var%d(t+%d)' % (j+1, i)) for j in range(n_vars)]
    # put it all together
    agg = concat(cols, axis=1)
    agg.columns = names
    # drop rows with NaN values
    if dropnan:
        agg.dropna(inplace=True)
    return agg

In [53]:
# load dataset
dataset = read_csv('C:/Users/*', header=0, index_col=0)
values = dataset.values

# ensure all data is float
values = values.astype('float32')

# normalize features
scaler = MinMaxScaler(feature_range=(0, 1))
scaled = scaler.fit_transform(values)

# specify the number of lag hours
n_hours = 2
n_features = 9

# frame as supervised learning
reframed = series_to_supervised(scaled, n_hours, 1)
print(reframed.shape)

reframed

(535, 27)


var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2     0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3     0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4     0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5     0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6     0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   
..         ...        ...        ...        ...        ...        ...   
532   0.647471   0.350071   0.683410   0.600138   0.604167   0.304962   
533   0.624708   0.579207   0.717050   0.770611   0.531250   0.351837   
534   0.797471   0.478075   0.801382   0.687265   0.781250   0.186211   
535   0.766732   0.534690   0.864055   0.749342   0.687500   0.286762   
536   0.690856   0.608430   0.800000   0.597099   0.791667   0.308640   

     var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  ...  var9(t-1)   var1(t)  \
2     0.001171   0.706132   0.735252   0.055642  ...   0.697631  0.075875   
3     0.000861   0.674529   0.697631   0.075875  ...   0.797491  0.103307   
4     0.000861   0.823113   0.797491   0.103307  ...   0.810961  0.176265   
5     0.003931   0.802359   0.810961   0.176265  ...   0.823037  0.143191   
6     0.001171   0.840095   0.823037   0.143191  ...   0.573618  0.144163   
..         ...        ...        ...        ...  ...        ...       ...   
532   0.015390   0.658019   0.671620   0.624708  ...   0.698095  0.797471   
533   0.000002   0.708019   0.698095   0.797471  ...   0.819786  0.766732   
534   0.075827   0.788679   0.819786   0.766732  ...   0.856014  0.690856   
535   0.000002   0.866982   0.856014   0.690856  ...   0.820714  0.663813   
536   0.090269   0.780190   0.820714   0.663813  ...   0.826753  0.792801   

      var2(t)   var3(t)   var4(t)   var5(t)   var6(t)   var7(t)   var8(t)  \
2    0.675534  0.822119  0.834066  0.541667  0.329227  0.000861  0.823113   
3    0.721197  0.808756  0.800696  0.677083  0.259926  0.003931  0.802359   
4    0.554569  0.833639  0.748459  0.697917  0.157902  0.001171  0.840095   
5    0.288067  0.575576  0.597859  0.500000  0.110291  0.190853  0.546227   
6    0.366840  0.649308  0.503348  0.656250  0.150917  0.132394  0.598114   
..        ...       ...       ...       ...       ...       ...       ...   
532  0.478075  0.801382  0.687265  0.781250  0.186211  0.075827  0.788679   
533  0.534690  0.864055  0.749342  0.687500  0.286762  0.000002  0.866982   
534  0.608430  0.800000  0.597099  0.791667  0.308640  0.090269  0.780190   
535  0.418575  0.819816  0.612433  0.729167  0.255695  0.000616  0.825472   
536  0.317628  0.627189  0.454131  0.572917  0.294670  0.002762  0.609907   

      var9(t)  
2    0.797491  
3    0.810961  
4    0.823037  
5    0.573618  
6    0.680910  
..        ...  
532  0.819786  
533  0.856014  
534  0.820714  
535  0.826753  
536  0.631677  

[535 rows x 27 columns]

In [54]:
# split into train and test sets
values = reframed.values
n_train_hours = 400
train = values[:n_train_hours, :]
test = values[n_train_hours:, :]
# split into input and outputs
n_obs = n_hours * n_features
train_X, train_y = train[:, :n_obs], train[:, -n_features]
test_X, test_y = test[:, :n_obs], test[:, -n_features]
print(train_X.shape, len(train_X), train_y.shape)
# reshape input to be 3D [samples, timesteps, features]
train_X = train_X.reshape((train_X.shape[0], n_hours, n_features))
test_X = test_X.reshape((test_X.shape[0], n_hours, n_features))
print(train_X.shape, train_y.shape, test_X.shape, test_y.shape)

(400, 18) 400 (400,)
(400, 2, 9) (400,) (135, 2, 9) (135,)


In [55]:
# drop columns we don't want to predict
#reframed.drop(reframed.columns[[55,56,57,58,59,60,61,62]], axis=1, inplace=True)
reframed.drop(reframed.columns[[19,20,21,22,23,24,25,26]], axis=1, inplace=True)
#reframed.drop(reframed.columns[[109,110,111,112,113,114,115,116]], axis=1, inplace=True)
print(reframed.head())

   var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2   0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3   0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4   0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5   0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6   0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   

   var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  var2(t-1)  var3(t-1)  \
2   0.001171   0.706132   0.735252   0.055642   0.368665   0.694469   
3   0.000861   0.674529   0.697631   0.075875   0.675534   0.822119   
4   0.000861   0.823113   0.797491   0.103307   0.721197   0.808756   
5   0.003931   0.802359   0.810961   0.176265   0.554569   0.833639   
6   0.001171   0.840095   0.823037   0.143191   0.288067   0.575576   

   var4(t-1)  var5(t-1)  var6(t-1)  var7(t-1)  var8(t-1)  var9(t-1)   var1(t)  
2   0.660572   0.468750   0.265625   0.000861   0.674529   0.69763

In [56]:
# create model
model = KerasRegressor(build_fn=create_model,epochs=100, batch_size=18, verbose=1)

In [57]:
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=3)
#grid_result = grid.fit(train_X, train_y)

from sklearn.model_selection import TimeSeriesSplit
tscv = TimeSeriesSplit(n_splits=3).get_n_splits([train_X, train_y])
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_squared_error')
grid_result = grid.fit(train_X, train_y)

#from sklearn.model_selection import TimeSeriesSplit
#tscv = TimeSeriesSplit(n_splits=3)
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_squared_error')
#grid_result = grid.fit(train_X, train_y)

Train on 266 samples
Epoch 1/100
266/266 [==============================] - 2s 9ms/sample - loss: 0.3000 - mae: 0.3000
Epoch 2/100
266/266 [==============================] - 0s 363us/sample - loss: 0.2511 - mae: 0.2511
Epoch 3/100
266/266 [==============================] - 0s 336us/sample - loss: 0.1207 - mae: 0.1207
Epoch 4/100
266/266 [==============================] - 0s 353us/sample - loss: 0.0935 - mae: 0.0935
Epoch 5/100
266/266 [==============================] - 0s 337us/sample - loss: 0.0843 - mae: 0.0843
Epoch 6/100
266/266 [==============================] - 0s 349us/sample - loss: 0.0785 - mae: 0.0785
Epoch 7/100
266/266 [==============================] - 0s 345us/sample - loss: 0.0754 - mae: 0.0754
Epoch 8/100
266/266 [==============================] - 0s 345us/sample - loss: 0.0696 - mae: 0.0696
Epoch 9/100
266/266 [==============================] - 0s 341us/sample - loss: 0.0669 - mae: 0.0669
Epoch 10/100
266/266 [==============================] - 0s 345us/sample - loss: 0

266/266 [==============================] - 0s 332us/sample - loss: 0.0431 - mae: 0.0431
Epoch 83/100
266/266 [==============================] - 0s 326us/sample - loss: 0.0428 - mae: 0.0428
Epoch 84/100
266/266 [==============================] - 0s 356us/sample - loss: 0.0403 - mae: 0.0403
Epoch 85/100
266/266 [==============================] - 0s 416us/sample - loss: 0.0411 - mae: 0.0411
Epoch 86/100
266/266 [==============================] - 0s 367us/sample - loss: 0.0423 - mae: 0.0423
Epoch 87/100
266/266 [==============================] - 0s 304us/sample - loss: 0.0403 - mae: 0.0403
Epoch 88/100
266/266 [==============================] - 0s 307us/sample - loss: 0.0390 - mae: 0.0390
Epoch 89/100
266/266 [==============================] - 0s 326us/sample - loss: 0.0405 - mae: 0.0405
Epoch 90/100
266/266 [==============================] - 0s 345us/sample - loss: 0.0384 - mae: 0.0384
Epoch 91/100
266/266 [==============================] - 0s 330us/sample - loss: 0.0382 - mae: 0.0382
Epo

267/267 [==============================] - 0s 355us/sample - loss: 0.0345 - mae: 0.0345
Epoch 43/100
267/267 [==============================] - 0s 340us/sample - loss: 0.0320 - mae: 0.0320
Epoch 44/100
267/267 [==============================] - 0s 342us/sample - loss: 0.0320 - mae: 0.0320
Epoch 45/100
267/267 [==============================] - 0s 325us/sample - loss: 0.0315 - mae: 0.0315
Epoch 46/100
267/267 [==============================] - 0s 342us/sample - loss: 0.0339 - mae: 0.0339
Epoch 47/100
267/267 [==============================] - 0s 339us/sample - loss: 0.0321 - mae: 0.0321
Epoch 48/100
267/267 [==============================] - 0s 344us/sample - loss: 0.0326 - mae: 0.0326
Epoch 49/100
267/267 [==============================] - 0s 340us/sample - loss: 0.0366 - mae: 0.0366
Epoch 50/100
267/267 [==============================] - 0s 336us/sample - loss: 0.0326 - mae: 0.0326
Epoch 51/100
267/267 [==============================] - 0s 339us/sample - loss: 0.0326 - mae: 0.0326
Epo

267/267 [==============================] - 0s 355us/sample - loss: 0.1890 - mae: 0.1890
Epoch 3/100
267/267 [==============================] - 0s 357us/sample - loss: 0.1367 - mae: 0.1367
Epoch 4/100
267/267 [==============================] - 0s 334us/sample - loss: 0.1302 - mae: 0.1302
Epoch 5/100
267/267 [==============================] - 0s 359us/sample - loss: 0.1272 - mae: 0.1272
Epoch 6/100
267/267 [==============================] - 0s 359us/sample - loss: 0.1212 - mae: 0.1212
Epoch 7/100
267/267 [==============================] - 0s 351us/sample - loss: 0.1129 - mae: 0.1129
Epoch 8/100
267/267 [==============================] - 0s 332us/sample - loss: 0.0979 - mae: 0.0979
Epoch 9/100
267/267 [==============================] - 0s 343us/sample - loss: 0.0781 - mae: 0.0781
Epoch 10/100
267/267 [==============================] - 0s 344us/sample - loss: 0.0593 - mae: 0.0593
Epoch 11/100
267/267 [==============================] - 0s 325us/sample - loss: 0.0586 - mae: 0.0586
Epoch 12/1

267/267 [==============================] - 0s 350us/sample - loss: 0.0302 - mae: 0.0302
Epoch 64/100
267/267 [==============================] - 0s 359us/sample - loss: 0.0294 - mae: 0.0294
Epoch 65/100
267/267 [==============================] - 0s 351us/sample - loss: 0.0298 - mae: 0.0298
Epoch 66/100
267/267 [==============================] - 0s 344us/sample - loss: 0.0308 - mae: 0.0308
Epoch 67/100
267/267 [==============================] - 0s 351us/sample - loss: 0.0295 - mae: 0.0295
Epoch 68/100
267/267 [==============================] - 0s 365us/sample - loss: 0.0295 - mae: 0.0295
Epoch 69/100
267/267 [==============================] - 0s 359us/sample - loss: 0.0291 - mae: 0.0291
Epoch 70/100
267/267 [==============================] - 0s 344us/sample - loss: 0.0289 - mae: 0.0289
Epoch 71/100
267/267 [==============================] - 0s 347us/sample - loss: 0.0289 - mae: 0.0289
Epoch 72/100
267/267 [==============================] - 0s 355us/sample - loss: 0.0293 - mae: 0.0293
Epo

...

267/267 [==============================] - 0s 336us/sample - loss: 0.0794 - mae: 0.0794
Epoch 3/100
267/267 [==============================] - 0s 352us/sample - loss: 0.0723 - mae: 0.0723
Epoch 4/100
267/267 [==============================] - 0s 362us/sample - loss: 0.0666 - mae: 0.0666
Epoch 5/100
267/267 [==============================] - 0s 344us/sample - loss: 0.0580 - mae: 0.0580
Epoch 6/100
267/267 [==============================] - 0s 362us/sample - loss: 0.0465 - mae: 0.0465
Epoch 7/100
267/267 [==============================] - 0s 359us/sample - loss: 0.0394 - mae: 0.0394
Epoch 8/100
267/267 [==============================] - 0s 359us/sample - loss: 0.0348 - mae: 0.0348
Epoch 9/100
267/267 [==============================] - 0s 351us/sample - loss: 0.0360 - mae: 0.0360
Epoch 10/100
267/267 [==============================] - 0s 359us/sample - loss: 0.0366 - mae: 0.0366
Epoch 11/100
267/267 [==============================] - 0s 347us/sample - loss: 0.0358 - mae: 0.0358
Epoch 12/1

266/266 [==============================] - 0s 364us/sample - loss: 0.0351 - mae: 0.0351
Epoch 64/100
266/266 [==============================] - 0s 356us/sample - loss: 0.0356 - mae: 0.0356
Epoch 65/100
266/266 [==============================] - 0s 367us/sample - loss: 0.0359 - mae: 0.0359
Epoch 66/100
266/266 [==============================] - 0s 353us/sample - loss: 0.0376 - mae: 0.0376
Epoch 67/100
266/266 [==============================] - 0s 362us/sample - loss: 0.0401 - mae: 0.0401
Epoch 68/100
266/266 [==============================] - 0s 350us/sample - loss: 0.0361 - mae: 0.0361
Epoch 69/100
266/266 [==============================] - 0s 367us/sample - loss: 0.0349 - mae: 0.0349
Epoch 70/100
266/266 [==============================] - 0s 367us/sample - loss: 0.0355 - mae: 0.0355
Epoch 71/100
266/266 [==============================] - 0s 371us/sample - loss: 0.0360 - mae: 0.0360
Epoch 72/100
266/266 [==============================] - 0s 364us/sample - loss: 0.0345 - mae: 0.0345
Epo

267/267 [==============================] - 0s 366us/sample - loss: 0.0306 - mae: 0.0306
Epoch 24/100
267/267 [==============================] - 0s 359us/sample - loss: 0.0340 - mae: 0.0340
Epoch 25/100
267/267 [==============================] - 0s 355us/sample - loss: 0.0325 - mae: 0.0325
Epoch 26/100
267/267 [==============================] - 0s 351us/sample - loss: 0.0321 - mae: 0.0321
Epoch 27/100
267/267 [==============================] - 0s 352us/sample - loss: 0.0305 - mae: 0.0305
Epoch 28/100
267/267 [==============================] - 0s 363us/sample - loss: 0.0325 - mae: 0.0325
Epoch 29/100
267/267 [==============================] - 0s 352us/sample - loss: 0.0317 - mae: 0.0317
Epoch 30/100
267/267 [==============================] - 0s 366us/sample - loss: 0.0304 - mae: 0.0304
Epoch 31/100
267/267 [==============================] - 0s 362us/sample - loss: 0.0326 - mae: 0.0326
Epoch 32/100
267/267 [==============================] - 0s 351us/sample - loss: 0.0345 - mae: 0.0345
Epo

266/266 [==============================] - 0s 345us/sample - loss: 0.0343 - mae: 0.0343
Epoch 85/100
266/266 [==============================] - 0s 352us/sample - loss: 0.0353 - mae: 0.0353
Epoch 86/100
266/266 [==============================] - 0s 350us/sample - loss: 0.0341 - mae: 0.0341
Epoch 87/100
266/266 [==============================] - 0s 357us/sample - loss: 0.0328 - mae: 0.0328
Epoch 88/100
266/266 [==============================] - 0s 367us/sample - loss: 0.0322 - mae: 0.0322
Epoch 89/100
266/266 [==============================] - 0s 356us/sample - loss: 0.0326 - mae: 0.0326
Epoch 90/100
266/266 [==============================] - 0s 360us/sample - loss: 0.0325 - mae: 0.0325
Epoch 91/100
266/266 [==============================] - 0s 356us/sample - loss: 0.0326 - mae: 0.0326
Epoch 92/100
266/266 [==============================] - 0s 360us/sample - loss: 0.0326 - mae: 0.0326
Epoch 93/100
266/266 [==============================] - 0s 360us/sample - loss: 0.0312 - mae: 0.0312
Epo

267/267 [==============================] - 0s 366us/sample - loss: 0.0291 - mae: 0.0291
Epoch 45/100
267/267 [==============================] - 0s 362us/sample - loss: 0.0308 - mae: 0.0308
Epoch 46/100
267/267 [==============================] - 0s 362us/sample - loss: 0.0305 - mae: 0.0305
Epoch 47/100
267/267 [==============================] - 0s 362us/sample - loss: 0.0289 - mae: 0.0289
Epoch 48/100
267/267 [==============================] - 0s 359us/sample - loss: 0.0290 - mae: 0.0290
Epoch 49/100
267/267 [==============================] - 0s 361us/sample - loss: 0.0365 - mae: 0.0365
Epoch 50/100
267/267 [==============================] - 0s 370us/sample - loss: 0.0330 - mae: 0.0330
Epoch 51/100
267/267 [==============================] - 0s 371us/sample - loss: 0.0295 - mae: 0.0295
Epoch 52/100
267/267 [==============================] - 0s 370us/sample - loss: 0.0281 - mae: 0.0281
Epoch 53/100
267/267 [==============================] - 0s 351us/sample - loss: 0.0288 - mae: 0.0288
Epo

In [58]:
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Best: -0.002842 using {'kernel_initializer': 'he_uniform'}
-0.003713 (0.001172) with: {'kernel_initializer': 'uniform'}
-0.003172 (0.000758) with: {'kernel_initializer': 'random_normal'}
-0.003496 (0.001034) with: {'kernel_initializer': 'random_uniform'}
-0.003627 (0.000850) with: {'kernel_initializer': 'truncated_normal'}
-1.154314 (0.223736) with: {'kernel_initializer': 'ones'}
-0.003101 (0.001301) with: {'kernel_initializer': 'identity'}
-0.003743 (0.001797) with: {'kernel_initializer': 'lecun_uniform'}
-0.003288 (0.000992) with: {'kernel_initializer': 'normal'}
-0.042627 (0.026866) with: {'kernel_initializer': 'zeros'}
-0.002976 (0.001276) with: {'kernel_initializer': 'glorot_normal'}
-0.002941 (0.001013) with: {'kernel_initializer': 'glorot_uniform'}
-0.003766 (0.002754) with: {'kernel_initializer': 'he_normal'}
-0.002842 (0.001301) with: {'kernel_initializer': 'he_uniform'}


In [12]:
import os
####*IMPORANT*: Have to do this line *before* importing tensorflow
os.environ['PYTHONHASHSEED']=str(1)
import numpy as np
import tensorflow as tf
import random

# Use scikit-learn to grid search the batch size and epochs
import numpy
from sklearn.model_selection import GridSearchCV
from tensorflow.keras.models import Sequential 
from tensorflow.keras.layers import Dense
from tensorflow.keras.wrappers.scikit_learn import KerasRegressor

# Function to create model, required for KerasClassifier
from math import sqrt
from numpy import concatenate
from matplotlib import pyplot
from pandas import read_csv
from pandas import DataFrame
from pandas import concat
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_squared_error
from tensorflow.keras.layers import LSTM
import keras
from tensorflow.keras.constraints import max_norm
from tensorflow.keras.layers import Dropout

def reset_random_seeds():
   os.environ['PYTHONHASHSEED']=str(1)
   tf.random.set_seed(1)
   np.random.seed(1)
   random.seed(1)

#make some random data
reset_random_seeds()
#np.random.rand(4)


# design network for tuning dropout rate
def create_model(dropout_rate=0.0, weight_constraint=0):
    model = Sequential()
    model.add(LSTM(50,kernel_initializer='normal',kernel_constraint=max_norm(weight_constraint), input_shape=(train_X.shape[1], train_X.shape[2])))
    model.add(Dropout(dropout_rate))
    model.add(Dense(1,kernel_initializer='normal'))
    #compile model
    model.compile(loss='mae', optimizer='adam', metrics=['mae']) # can be mse or mae
    return model

In [2]:
# design network
reset_random_seeds()
def create_model(dropout_rate=0.0, weight_constraint=0):
    model = Sequential()
    model.add(LSTM(50,kernel_initializer='normal', kernel_constraint=max_norm(weight_constraint), return_sequences=True, input_shape=(train_X.shape[1], train_X.shape[2])))
    model.add(Dropout(dropout_rate))
    model.add(LSTM(50))
    model.add(Dense(10))
    model.add(Dense(1,kernel_initializer='normal'))
    #mse or mae it got better with mae
    model.compile(loss='mae', optimizer='adam', metrics=['mae']) # can be mse or mae
    return model

In [13]:
weight_constraint = [0, 1, 2, 3, 4, 5]
dropout_rate = [0.0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]
param_grid = dict(dropout_rate=dropout_rate, weight_constraint=weight_constraint)

In [14]:
# fix random seed for reproducibility
seed = 1 #seed 7
numpy.random.seed(seed)
#numpy.random.rand(4)

# convert series to supervised learning
def series_to_supervised(data, n_in=1, n_out=1, dropnan=True):
    n_vars = 1 if type(data) is list else data.shape[1]
    df = DataFrame(data)
    cols, names = list(), list()
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
        cols.append(df.shift(i))
        names += [('var%d(t-%d)' % (j+1, i)) for j in range(n_vars)]
    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df.shift(-i))
        if i == 0:
            names += [('var%d(t)' % (j+1)) for j in range(n_vars)]
        else:
            names += [('var%d(t+%d)' % (j+1, i)) for j in range(n_vars)]
    # put it all together
    agg = concat(cols, axis=1)
    agg.columns = names
    # drop rows with NaN values
    if dropnan:
        agg.dropna(inplace=True)
    return agg

In [15]:
# load dataset
dataset = read_csv('C:/Users/*', header=0, index_col=0)
values = dataset.values

# ensure all data is float
values = values.astype('float32')

# normalize features
scaler = MinMaxScaler(feature_range=(0, 1))
scaled = scaler.fit_transform(values)

# specify the number of lag hours
n_hours = 2
n_features = 9

# frame as supervised learning
reframed = series_to_supervised(scaled, n_hours, 1)
print(reframed.shape)

reframed

(535, 27)


var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2     0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3     0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4     0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5     0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6     0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   
..         ...        ...        ...        ...        ...        ...   
532   0.647471   0.350071   0.683410   0.600138   0.604167   0.304962   
533   0.624708   0.579207   0.717050   0.770611   0.531250   0.351837   
534   0.797471   0.478075   0.801382   0.687265   0.781250   0.186211   
535   0.766732   0.534690   0.864055   0.749342   0.687500   0.286762   
536   0.690856   0.608430   0.800000   0.597099   0.791667   0.308640   

     var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  ...  var9(t-1)   var1(t)  \
2     0.001171   0.706132   0.735252   0.055642  ...   0.697631  0.075875   
3     0.000861   0.674529   0.697631   0.075875  ...   0.797491  0.103307   
4     0.000861   0.823113   0.797491   0.103307  ...   0.810961  0.176265   
5     0.003931   0.802359   0.810961   0.176265  ...   0.823037  0.143191   
6     0.001171   0.840095   0.823037   0.143191  ...   0.573618  0.144163   
..         ...        ...        ...        ...  ...        ...       ...   
532   0.015390   0.658019   0.671620   0.624708  ...   0.698095  0.797471   
533   0.000002   0.708019   0.698095   0.797471  ...   0.819786  0.766732   
534   0.075827   0.788679   0.819786   0.766732  ...   0.856014  0.690856   
535   0.000002   0.866982   0.856014   0.690856  ...   0.820714  0.663813   
536   0.090269   0.780190   0.820714   0.663813  ...   0.826753  0.792801   

      var2(t)   var3(t)   var4(t)   var5(t)   var6(t)   var7(t)   var8(t)  \
2    0.675534  0.822119  0.834066  0.541667  0.329227  0.000861  0.823113   
3    0.721197  0.808756  0.800696  0.677083  0.259926  0.003931  0.802359   
4    0.554569  0.833639  0.748459  0.697917  0.157902  0.001171  0.840095   
5    0.288067  0.575576  0.597859  0.500000  0.110291  0.190853  0.546227   
6    0.366840  0.649308  0.503348  0.656250  0.150917  0.132394  0.598114   
..        ...       ...       ...       ...       ...       ...       ...   
532  0.478075  0.801382  0.687265  0.781250  0.186211  0.075827  0.788679   
533  0.534690  0.864055  0.749342  0.687500  0.286762  0.000002  0.866982   
534  0.608430  0.800000  0.597099  0.791667  0.308640  0.090269  0.780190   
535  0.418575  0.819816  0.612433  0.729167  0.255695  0.000616  0.825472   
536  0.317628  0.627189  0.454131  0.572917  0.294670  0.002762  0.609907   

      var9(t)  
2    0.797491  
3    0.810961  
4    0.823037  
5    0.573618  
6    0.680910  
..        ...  
532  0.819786  
533  0.856014  
534  0.820714  
535  0.826753  
536  0.631677  

[535 rows x 27 columns]

In [16]:
# split into train and test sets
values = reframed.values
n_train_hours = 400
train = values[:n_train_hours, :]
test = values[n_train_hours:, :]
# split into input and outputs
n_obs = n_hours * n_features
train_X, train_y = train[:, :n_obs], train[:, -n_features]
test_X, test_y = test[:, :n_obs], test[:, -n_features]
print(train_X.shape, len(train_X), train_y.shape)
# reshape input to be 3D [samples, timesteps, features]
train_X = train_X.reshape((train_X.shape[0], n_hours, n_features))
test_X = test_X.reshape((test_X.shape[0], n_hours, n_features))
print(train_X.shape, train_y.shape, test_X.shape, test_y.shape)

(400, 18) 400 (400,)
(400, 2, 9) (400,) (135, 2, 9) (135,)


In [17]:
# drop columns we don't want to predict
#reframed.drop(reframed.columns[[55,56,57,58,59,60,61,62]], axis=1, inplace=True)
reframed.drop(reframed.columns[[19,20,21,22,23,24,25,26]], axis=1, inplace=True)
#reframed.drop(reframed.columns[[109,110,111,112,113,114,115,116]], axis=1, inplace=True)
print(reframed.head())

   var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2   0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3   0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4   0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5   0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6   0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   

   var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  var2(t-1)  var3(t-1)  \
2   0.001171   0.706132   0.735252   0.055642   0.368665   0.694469   
3   0.000861   0.674529   0.697631   0.075875   0.675534   0.822119   
4   0.000861   0.823113   0.797491   0.103307   0.721197   0.808756   
5   0.003931   0.802359   0.810961   0.176265   0.554569   0.833639   
6   0.001171   0.840095   0.823037   0.143191   0.288067   0.575576   

   var4(t-1)  var5(t-1)  var6(t-1)  var7(t-1)  var8(t-1)  var9(t-1)   var1(t)  
2   0.660572   0.468750   0.265625   0.000861   0.674529   0.69763

In [18]:
# create model
model = KerasRegressor(build_fn=create_model,epochs=100, batch_size=18, verbose=1)

In [19]:
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=3)
#grid_result = grid.fit(train_X, train_y)

from sklearn.model_selection import TimeSeriesSplit
tscv = TimeSeriesSplit(n_splits=3).get_n_splits([train_X, train_y])
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_squared_error')
grid_result = grid.fit(train_X, train_y)

#from sklearn.model_selection import TimeSeriesSplit
#tscv = TimeSeriesSplit(n_splits=3)
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_squared_error')
#grid_result = grid.fit(train_X, train_y)

Train on 266 samples
Epoch 1/100
266/266 [==============================] - 4s 17ms/sample - loss: 0.2977 - mae: 0.2977
Epoch 2/100
266/266 [==============================] - 0s 296us/sample - loss: 0.2630 - mae: 0.2630
Epoch 3/100
266/266 [==============================] - 0s 311us/sample - loss: 0.2051 - mae: 0.2051
Epoch 4/100
266/266 [==============================] - 0s 254us/sample - loss: 0.1376 - mae: 0.1376
Epoch 5/100
266/266 [==============================] - 0s 281us/sample - loss: 0.1269 - mae: 0.1269
Epoch 6/100
266/266 [==============================] - 0s 322us/sample - loss: 0.1273 - mae: 0.1273
Epoch 7/100
266/266 [==============================] - 0s 307us/sample - loss: 0.1257 - mae: 0.1257
Epoch 8/100
266/266 [==============================] - 0s 322us/sample - loss: 0.1257 - mae: 0.1257
Epoch 9/100
266/266 [==============================] - 0s 282us/sample - loss: 0.1255 - mae: 0.1255
Epoch 10/100
266/266 [==============================] - 0s 271us/sample - loss: 

267/267 [==============================] - 0s 366us/sample - loss: 0.1434 - mae: 0.1434
Epoch 62/100
267/267 [==============================] - 0s 315us/sample - loss: 0.1437 - mae: 0.1437
Epoch 63/100
267/267 [==============================] - 0s 339us/sample - loss: 0.1436 - mae: 0.1436
Epoch 64/100
267/267 [==============================] - 0s 335us/sample - loss: 0.1434 - mae: 0.1434
Epoch 65/100
267/267 [==============================] - 0s 345us/sample - loss: 0.1429 - mae: 0.1429
Epoch 66/100
267/267 [==============================] - 0s 312us/sample - loss: 0.1431 - mae: 0.1431
Epoch 67/100
267/267 [==============================] - 0s 345us/sample - loss: 0.1434 - mae: 0.1434
Epoch 68/100
267/267 [==============================] - 0s 311us/sample - loss: 0.1427 - mae: 0.1427
Epoch 69/100
267/267 [==============================] - 0s 335us/sample - loss: 0.1433 - mae: 0.1433
Epoch 70/100
267/267 [==============================] - 0s 399us/sample - loss: 0.1434 - mae: 0.1434
Epo

266/266 [==============================] - 0s 337us/sample - loss: 0.0484 - mae: 0.0484
Epoch 22/100
266/266 [==============================] - 0s 283us/sample - loss: 0.0470 - mae: 0.0470
Epoch 23/100
266/266 [==============================] - 0s 322us/sample - loss: 0.0476 - mae: 0.0476
Epoch 24/100
266/266 [==============================] - 0s 311us/sample - loss: 0.0479 - mae: 0.0479
Epoch 25/100
266/266 [==============================] - 0s 299us/sample - loss: 0.0452 - mae: 0.0452
Epoch 26/100
266/266 [==============================] - 0s 290us/sample - loss: 0.0480 - mae: 0.0480
Epoch 27/100
266/266 [==============================] - 0s 297us/sample - loss: 0.0472 - mae: 0.0472
Epoch 28/100
266/266 [==============================] - 0s 366us/sample - loss: 0.0446 - mae: 0.0446
Epoch 29/100
266/266 [==============================] - 0s 277us/sample - loss: 0.0460 - mae: 0.0460
Epoch 30/100
266/266 [==============================] - 0s 299us/sample - loss: 0.0475 - mae: 0.0475
Epo

267/267 [==============================] - 0s 322us/sample - loss: 0.0366 - mae: 0.0366
Epoch 83/100
267/267 [==============================] - 0s 312us/sample - loss: 0.0354 - mae: 0.0354
Epoch 84/100
267/267 [==============================] - 0s 337us/sample - loss: 0.0356 - mae: 0.0356
Epoch 85/100
267/267 [==============================] - 0s 319us/sample - loss: 0.0360 - mae: 0.0360
Epoch 86/100
267/267 [==============================] - 0s 302us/sample - loss: 0.0367 - mae: 0.0367
Epoch 87/100
267/267 [==============================] - 0s 287us/sample - loss: 0.0363 - mae: 0.0363
Epoch 88/100
267/267 [==============================] - 0s 269us/sample - loss: 0.0349 - mae: 0.0349
Epoch 89/100
267/267 [==============================] - 0s 309us/sample - loss: 0.0361 - mae: 0.0361
Epoch 90/100
267/267 [==============================] - 0s 311us/sample - loss: 0.0353 - mae: 0.0353
Epoch 91/100
267/267 [==============================] - 0s 322us/sample - loss: 0.0363 - mae: 0.0363
Epo

266/266 [==============================] - 0s 338us/sample - loss: 0.0441 - mae: 0.0441
Epoch 43/100
266/266 [==============================] - 0s 309us/sample - loss: 0.0430 - mae: 0.0430
Epoch 44/100
266/266 [==============================] - 0s 321us/sample - loss: 0.0433 - mae: 0.0433
Epoch 45/100
266/266 [==============================] - 0s 328us/sample - loss: 0.0425 - mae: 0.0425
Epoch 46/100
266/266 [==============================] - 0s 322us/sample - loss: 0.0442 - mae: 0.0442
Epoch 47/100
266/266 [==============================] - 0s 352us/sample - loss: 0.0431 - mae: 0.0431
Epoch 48/100
266/266 [==============================] - 0s 327us/sample - loss: 0.0422 - mae: 0.0422
Epoch 49/100
266/266 [==============================] - 0s 318us/sample - loss: 0.0434 - mae: 0.0434
Epoch 50/100
266/266 [==============================] - 0s 299us/sample - loss: 0.0443 - mae: 0.0443
Epoch 51/100
266/266 [==============================] - 0s 273us/sample - loss: 0.0455 - mae: 0.0455
Epo

...

266/266 [==============================] - 0s 322us/sample - loss: 0.0673 - mae: 0.0673
Epoch 57/100
266/266 [==============================] - 0s 352us/sample - loss: 0.0682 - mae: 0.0682
Epoch 58/100
266/266 [==============================] - 0s 340us/sample - loss: 0.0681 - mae: 0.0681
Epoch 59/100
266/266 [==============================] - 0s 321us/sample - loss: 0.0691 - mae: 0.0691
Epoch 60/100
266/266 [==============================] - 0s 317us/sample - loss: 0.0690 - mae: 0.0690
Epoch 61/100
266/266 [==============================] - 0s 306us/sample - loss: 0.0682 - mae: 0.0682
Epoch 62/100
266/266 [==============================] - 0s 300us/sample - loss: 0.0658 - mae: 0.0658
Epoch 63/100
266/266 [==============================] - 0s 316us/sample - loss: 0.0710 - mae: 0.0710
Epoch 64/100
266/266 [==============================] - 0s 319us/sample - loss: 0.0717 - mae: 0.0717
Epoch 65/100
266/266 [==============================] - 0s 245us/sample - loss: 0.0618 - mae: 0.0618
Epo

267/267 [==============================] - 0s 308us/sample - loss: 0.0774 - mae: 0.0774
Epoch 16/100
267/267 [==============================] - 0s 297us/sample - loss: 0.0791 - mae: 0.0791
Epoch 17/100
267/267 [==============================] - 0s 308us/sample - loss: 0.0715 - mae: 0.0715
Epoch 18/100
267/267 [==============================] - 0s 315us/sample - loss: 0.0718 - mae: 0.0718
Epoch 19/100
267/267 [==============================] - 0s 322us/sample - loss: 0.0737 - mae: 0.0737
Epoch 20/100
267/267 [==============================] - 0s 316us/sample - loss: 0.0709 - mae: 0.0709
Epoch 21/100
267/267 [==============================] - 0s 312us/sample - loss: 0.0661 - mae: 0.0661
Epoch 22/100
267/267 [==============================] - 0s 319us/sample - loss: 0.0647 - mae: 0.0647
Epoch 23/100
267/267 [==============================] - 0s 289us/sample - loss: 0.0601 - mae: 0.0601
Epoch 24/100
267/267 [==============================] - 0s 367us/sample - loss: 0.0673 - mae: 0.0673
Epo

266/266 [==============================] - 0s 322us/sample - loss: 0.0623 - mae: 0.0623
Epoch 75/100
266/266 [==============================] - 0s 328us/sample - loss: 0.0674 - mae: 0.0674
Epoch 76/100
266/266 [==============================] - 0s 326us/sample - loss: 0.0646 - mae: 0.0646
Epoch 77/100
266/266 [==============================] - 0s 359us/sample - loss: 0.0601 - mae: 0.0601
Epoch 78/100
266/266 [==============================] - 0s 283us/sample - loss: 0.0722 - mae: 0.0722
Epoch 79/100
266/266 [==============================] - 0s 334us/sample - loss: 0.0607 - mae: 0.0607
Epoch 80/100
266/266 [==============================] - 0s 337us/sample - loss: 0.0670 - mae: 0.0670
Epoch 81/100
266/266 [==============================] - 0s 296us/sample - loss: 0.0691 - mae: 0.0691
Epoch 82/100
266/266 [==============================] - 0s 392us/sample - loss: 0.0634 - mae: 0.0634
Epoch 83/100
266/266 [==============================] - 0s 317us/sample - loss: 0.0674 - mae: 0.0674
Epo

267/267 [==============================] - 0s 301us/sample - loss: 0.0488 - mae: 0.0488
Epoch 35/100
267/267 [==============================] - 0s 301us/sample - loss: 0.0509 - mae: 0.0509
Epoch 36/100
267/267 [==============================] - 0s 309us/sample - loss: 0.0553 - mae: 0.0553
Epoch 37/100
267/267 [==============================] - 0s 312us/sample - loss: 0.0503 - mae: 0.0503
Epoch 38/100
267/267 [==============================] - 0s 319us/sample - loss: 0.0541 - mae: 0.0541
Epoch 39/100
267/267 [==============================] - 0s 323us/sample - loss: 0.0514 - mae: 0.0514
Epoch 40/100
267/267 [==============================] - 0s 316us/sample - loss: 0.0490 - mae: 0.0490
Epoch 41/100
267/267 [==============================] - 0s 309us/sample - loss: 0.0490 - mae: 0.0490
Epoch 42/100
267/267 [==============================] - 0s 314us/sample - loss: 0.0526 - mae: 0.0526
Epoch 43/100
267/267 [==============================] - 0s 306us/sample - loss: 0.0512 - mae: 0.0512
Epo

Epoch 95/100
400/400 [==============================] - 0s 270us/sample - loss: 0.0303 - mae: 0.0303
Epoch 96/100
400/400 [==============================] - 0s 323us/sample - loss: 0.0332 - mae: 0.0332
Epoch 97/100
400/400 [==============================] - 0s 304us/sample - loss: 0.0308 - mae: 0.0308
Epoch 98/100
400/400 [==============================] - 0s 320us/sample - loss: 0.0311 - mae: 0.0311
Epoch 99/100
400/400 [==============================] - 0s 344us/sample - loss: 0.0308 - mae: 0.0308
Epoch 100/100
400/400 [==============================] - 0s 268us/sample - loss: 0.0314 - mae: 0.0314


In [20]:
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Best: -0.002570 using {'dropout_rate': 0.0, 'weight_constraint': 5}
-0.041929 (0.026861) with: {'dropout_rate': 0.0, 'weight_constraint': 0}
-0.003077 (0.000633) with: {'dropout_rate': 0.0, 'weight_constraint': 1}
-0.002954 (0.000711) with: {'dropout_rate': 0.0, 'weight_constraint': 2}
-0.002699 (0.000699) with: {'dropout_rate': 0.0, 'weight_constraint': 3}
-0.002773 (0.000787) with: {'dropout_rate': 0.0, 'weight_constraint': 4}
-0.002570 (0.000499) with: {'dropout_rate': 0.0, 'weight_constraint': 5}
-0.041939 (0.028070) with: {'dropout_rate': 0.1, 'weight_constraint': 0}
-0.002846 (0.000589) with: {'dropout_rate': 0.1, 'weight_constraint': 1}
-0.003027 (0.000625) with: {'dropout_rate': 0.1, 'weight_constraint': 2}
-0.002718 (0.000712) with: {'dropout_rate': 0.1, 'weight_constraint': 3}
-0.002936 (0.001013) with: {'dropout_rate': 0.1, 'weight_constraint': 4}
-0.002731 (0.000574) with: {'dropout_rate': 0.1, 'weight_constraint': 5}
-0.041979 (0.027746) with: {'dropout_rate': 0.2, 'weight

In [21]:
import os
####*IMPORANT*: Have to do this line *before* importing tensorflow
os.environ['PYTHONHASHSEED']=str(1)
import numpy as np
import tensorflow as tf
import random

# Use scikit-learn to grid search the batch size and epochs
import numpy
from sklearn.model_selection import GridSearchCV
from tensorflow.keras.models import Sequential 
from tensorflow.keras.layers import Dense
from tensorflow.keras.wrappers.scikit_learn import KerasRegressor

# Function to create model, required for KerasClassifier
from math import sqrt
from numpy import concatenate
from matplotlib import pyplot
from pandas import read_csv
from pandas import DataFrame
from pandas import concat
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import mean_squared_error
from tensorflow.keras.layers import LSTM
import keras
from tensorflow.keras.constraints import max_norm
from tensorflow.keras.layers import Dropout

def reset_random_seeds():
   os.environ['PYTHONHASHSEED']=str(1)
   tf.random.set_seed(1)
   np.random.seed(1)
   random.seed(1)

#make some random data
reset_random_seeds()
#np.random.rand(4)


# design network for tuning dropout rate
def create_model(neurons=1):
    model = Sequential()
    model.add(LSTM(neurons,kernel_initializer='normal', input_shape=(train_X.shape[1], train_X.shape[2])))
    model.add(Dense(1,kernel_initializer='normal'))
    #compile model
    model.compile(loss='mae', optimizer='adam', metrics=['mae']) # can be mse or mae
    return model

In [30]:
# design network
reset_random_seeds()
def create_model(neurons=1):
    model = Sequential()
    model.add(LSTM(neurons,kernel_initializer='normal', return_sequences=True, input_shape=(train_X.shape[1], train_X.shape[2])))
    model.add(LSTM(50))
    model.add(Dense(10))
    model.add(Dense(1,kernel_initializer='normal'))
    #mse or mae it got better with mae
    model.compile(loss='mae', optimizer='adam', metrics=['mae']) # can be mse or mae
    return model

In [31]:
neurons = [1, 5, 10, 15, 20, 25, 30, 50, 60,100,128, 200,300]
#neurons2 = [1, 5, 10, 15, 20, 25, 30, 50, 128, 200, 300]

param_grid = dict(neurons=neurons)

In [32]:
# fix random seed for reproducibility
seed = 1 #seed 7
numpy.random.seed(seed)
#numpy.random.rand(4)

# convert series to supervised learning
def series_to_supervised(data, n_in=1, n_out=1, dropnan=True):
    n_vars = 1 if type(data) is list else data.shape[1]
    df = DataFrame(data)
    cols, names = list(), list()
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
        cols.append(df.shift(i))
        names += [('var%d(t-%d)' % (j+1, i)) for j in range(n_vars)]
    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df.shift(-i))
        if i == 0:
            names += [('var%d(t)' % (j+1)) for j in range(n_vars)]
        else:
            names += [('var%d(t+%d)' % (j+1, i)) for j in range(n_vars)]
    # put it all together
    agg = concat(cols, axis=1)
    agg.columns = names
    # drop rows with NaN values
    if dropnan:
        agg.dropna(inplace=True)
    return agg

In [33]:
# load dataset
dataset = read_csv('C:/Users/*', header=0, index_col=0)
values = dataset.values

# ensure all data is float
values = values.astype('float32')

# normalize features
scaler = MinMaxScaler(feature_range=(0, 1))
scaled = scaler.fit_transform(values)

# specify the number of lag hours
n_hours = 2
n_features = 9

# frame as supervised learning
reframed = series_to_supervised(scaled, n_hours, 1)
print(reframed.shape)

reframed

(535, 27)


var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2     0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3     0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4     0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5     0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6     0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   
..         ...        ...        ...        ...        ...        ...   
532   0.647471   0.350071   0.683410   0.600138   0.604167   0.304962   
533   0.624708   0.579207   0.717050   0.770611   0.531250   0.351837   
534   0.797471   0.478075   0.801382   0.687265   0.781250   0.186211   
535   0.766732   0.534690   0.864055   0.749342   0.687500   0.286762   
536   0.690856   0.608430   0.800000   0.597099   0.791667   0.308640   

     var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  ...  var9(t-1)   var1(t)  \
2     0.001171   0.706132   0.735252   0.055642  ...   0.697631  0.075875   
3     0.000861   0.674529   0.697631   0.075875  ...   0.797491  0.103307   
4     0.000861   0.823113   0.797491   0.103307  ...   0.810961  0.176265   
5     0.003931   0.802359   0.810961   0.176265  ...   0.823037  0.143191   
6     0.001171   0.840095   0.823037   0.143191  ...   0.573618  0.144163   
..         ...        ...        ...        ...  ...        ...       ...   
532   0.015390   0.658019   0.671620   0.624708  ...   0.698095  0.797471   
533   0.000002   0.708019   0.698095   0.797471  ...   0.819786  0.766732   
534   0.075827   0.788679   0.819786   0.766732  ...   0.856014  0.690856   
535   0.000002   0.866982   0.856014   0.690856  ...   0.820714  0.663813   
536   0.090269   0.780190   0.820714   0.663813  ...   0.826753  0.792801   

      var2(t)   var3(t)   var4(t)   var5(t)   var6(t)   var7(t)   var8(t)  \
2    0.675534  0.822119  0.834066  0.541667  0.329227  0.000861  0.823113   
3    0.721197  0.808756  0.800696  0.677083  0.259926  0.003931  0.802359   
4    0.554569  0.833639  0.748459  0.697917  0.157902  0.001171  0.840095   
5    0.288067  0.575576  0.597859  0.500000  0.110291  0.190853  0.546227   
6    0.366840  0.649308  0.503348  0.656250  0.150917  0.132394  0.598114   
..        ...       ...       ...       ...       ...       ...       ...   
532  0.478075  0.801382  0.687265  0.781250  0.186211  0.075827  0.788679   
533  0.534690  0.864055  0.749342  0.687500  0.286762  0.000002  0.866982   
534  0.608430  0.800000  0.597099  0.791667  0.308640  0.090269  0.780190   
535  0.418575  0.819816  0.612433  0.729167  0.255695  0.000616  0.825472   
536  0.317628  0.627189  0.454131  0.572917  0.294670  0.002762  0.609907   

      var9(t)  
2    0.797491  
3    0.810961  
4    0.823037  
5    0.573618  
6    0.680910  
..        ...  
532  0.819786  
533  0.856014  
534  0.820714  
535  0.826753  
536  0.631677  

[535 rows x 27 columns]

In [34]:
# split into train and test sets
values = reframed.values
n_train_hours = 400
train = values[:n_train_hours, :]
test = values[n_train_hours:, :]
# split into input and outputs
n_obs = n_hours * n_features
train_X, train_y = train[:, :n_obs], train[:, -n_features]
test_X, test_y = test[:, :n_obs], test[:, -n_features]
print(train_X.shape, len(train_X), train_y.shape)
# reshape input to be 3D [samples, timesteps, features]
train_X = train_X.reshape((train_X.shape[0], n_hours, n_features))
test_X = test_X.reshape((test_X.shape[0], n_hours, n_features))
print(train_X.shape, train_y.shape, test_X.shape, test_y.shape)

(400, 18) 400 (400,)
(400, 2, 9) (400,) (135, 2, 9) (135,)


In [35]:
# drop columns we don't want to predict
#reframed.drop(reframed.columns[[55,56,57,58,59,60,61,62]], axis=1, inplace=True)
reframed.drop(reframed.columns[[19,20,21,22,23,24,25,26]], axis=1, inplace=True)
#reframed.drop(reframed.columns[[109,110,111,112,113,114,115,116]], axis=1, inplace=True)
print(reframed.head())

   var1(t-2)  var2(t-2)  var3(t-2)  var4(t-2)  var5(t-2)  var6(t-2)  \
2   0.025486   0.615296   0.732719   0.726748   0.552083   0.261765   
3   0.055642   0.368665   0.694469   0.660572   0.468750   0.265625   
4   0.075875   0.675534   0.822119   0.834066   0.541667   0.329227   
5   0.103307   0.721197   0.808756   0.800696   0.677083   0.259926   
6   0.176265   0.554569   0.833639   0.748459   0.697917   0.157902   

   var7(t-2)  var8(t-2)  var9(t-2)  var1(t-1)  var2(t-1)  var3(t-1)  \
2   0.001171   0.706132   0.735252   0.055642   0.368665   0.694469   
3   0.000861   0.674529   0.697631   0.075875   0.675534   0.822119   
4   0.000861   0.823113   0.797491   0.103307   0.721197   0.808756   
5   0.003931   0.802359   0.810961   0.176265   0.554569   0.833639   
6   0.001171   0.840095   0.823037   0.143191   0.288067   0.575576   

   var4(t-1)  var5(t-1)  var6(t-1)  var7(t-1)  var8(t-1)  var9(t-1)   var1(t)  
2   0.660572   0.468750   0.265625   0.000861   0.674529   0.69763

In [36]:
# create model
model = KerasRegressor(build_fn=create_model,epochs=100, batch_size=18, verbose=1)

In [37]:
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=3)
#grid_result = grid.fit(train_X, train_y)

from sklearn.model_selection import TimeSeriesSplit
tscv = TimeSeriesSplit(n_splits=3)
grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_squared_error')
grid_result = grid.fit(train_X, train_y)

#from sklearn.model_selection import TimeSeriesSplit
#tscv = TimeSeriesSplit(n_splits=3)
#grid = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=1, cv=tscv, scoring = 'neg_mean_squared_error')
#grid_result = grid.fit(train_X, train_y)

Train on 266 samples
Epoch 1/100
266/266 [==============================] - 9s 33ms/sample - loss: 0.2943 - mae: 0.2943
Epoch 2/100
266/266 [==============================] - 0s 444us/sample - loss: 0.2415 - mae: 0.2415
Epoch 3/100
266/266 [==============================] - 0s 421us/sample - loss: 0.1577 - mae: 0.1577
Epoch 4/100
266/266 [==============================] - 0s 456us/sample - loss: 0.1249 - mae: 0.1249
Epoch 5/100
266/266 [==============================] - 0s 439us/sample - loss: 0.1245 - mae: 0.1245
Epoch 6/100
266/266 [==============================] - 0s 443us/sample - loss: 0.1208 - mae: 0.1208
Epoch 7/100
266/266 [==============================] - 0s 455us/sample - loss: 0.1135 - mae: 0.1135
Epoch 8/100
266/266 [==============================] - 0s 454us/sample - loss: 0.1055 - mae: 0.1055
Epoch 9/100
266/266 [==============================] - 0s 422us/sample - loss: 0.0973 - mae: 0.0973
Epoch 10/100
266/266 [==============================] - 0s 454us/sample - loss: 

266/266 [==============================] - 0s 428us/sample - loss: 0.0466 - mae: 0.0466
Epoch 83/100
266/266 [==============================] - 0s 455us/sample - loss: 0.0464 - mae: 0.0464
Epoch 84/100
266/266 [==============================] - 0s 403us/sample - loss: 0.0461 - mae: 0.0461
Epoch 85/100
266/266 [==============================] - 0s 485us/sample - loss: 0.0466 - mae: 0.0466
Epoch 86/100
266/266 [==============================] - 0s 456us/sample - loss: 0.0461 - mae: 0.0461
Epoch 87/100
266/266 [==============================] - 0s 479us/sample - loss: 0.0454 - mae: 0.0454
Epoch 88/100
266/266 [==============================] - 0s 473us/sample - loss: 0.0454 - mae: 0.0454
Epoch 89/100
266/266 [==============================] - 0s 517us/sample - loss: 0.0465 - mae: 0.0465
Epoch 90/100
266/266 [==============================] - 0s 426us/sample - loss: 0.0455 - mae: 0.0455
Epoch 91/100
266/266 [==============================] - 0s 449us/sample - loss: 0.0456 - mae: 0.0456
Epo

267/267 [==============================] - 0s 491us/sample - loss: 0.0373 - mae: 0.0373
Epoch 43/100
267/267 [==============================] - 0s 444us/sample - loss: 0.0354 - mae: 0.0354
Epoch 44/100
267/267 [==============================] - 0s 421us/sample - loss: 0.0358 - mae: 0.0358
Epoch 45/100
267/267 [==============================] - 0s 441us/sample - loss: 0.0377 - mae: 0.0377
Epoch 46/100
267/267 [==============================] - 0s 445us/sample - loss: 0.0373 - mae: 0.0373
Epoch 47/100
267/267 [==============================] - 0s 404us/sample - loss: 0.0349 - mae: 0.0349
Epoch 48/100
267/267 [==============================] - 0s 442us/sample - loss: 0.0354 - mae: 0.0354
Epoch 49/100
267/267 [==============================] - 0s 445us/sample - loss: 0.0354 - mae: 0.0354
Epoch 50/100
267/267 [==============================] - 0s 414us/sample - loss: 0.0338 - mae: 0.0338
Epoch 51/100
267/267 [==============================] - 0s 469us/sample - loss: 0.0344 - mae: 0.0344
Epo

Epoch 22/100
266/266 [==============================] - 0s 489us/sample - loss: 0.0624 - mae: 0.0624
Epoch 23/100
266/266 [==============================] - 0s 495us/sample - loss: 0.0631 - mae: 0.0631
Epoch 24/100
266/266 [==============================] - 0s 526us/sample - loss: 0.0599 - mae: 0.0599
Epoch 25/100
266/266 [==============================] - 0s 595us/sample - loss: 0.0585 - mae: 0.0585
Epoch 26/100
266/266 [==============================] - 0s 429us/sample - loss: 0.0594 - mae: 0.0594
Epoch 27/100
266/266 [==============================] - 0s 543us/sample - loss: 0.0576 - mae: 0.0576
Epoch 28/100
266/266 [==============================] - 0s 562us/sample - loss: 0.0577 - mae: 0.0577
Epoch 29/100
266/266 [==============================] - 0s 530us/sample - loss: 0.0583 - mae: 0.0583
Epoch 30/100
266/266 [==============================] - 0s 553us/sample - loss: 0.0548 - mae: 0.0548
Epoch 31/100
266/266 [==============================] - 0s 513us/sample - loss: 0.0550 - ma

267/267 [==============================] - 0s 191us/sample - loss: 0.0387 - mae: 0.0387
Epoch 84/100
267/267 [==============================] - 0s 187us/sample - loss: 0.0392 - mae: 0.0392
Epoch 85/100
267/267 [==============================] - 0s 176us/sample - loss: 0.0388 - mae: 0.0388
Epoch 86/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0388 - mae: 0.0388
Epoch 87/100
267/267 [==============================] - 0s 176us/sample - loss: 0.0400 - mae: 0.0400
Epoch 88/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0380 - mae: 0.0380
Epoch 89/100
267/267 [==============================] - 0s 213us/sample - loss: 0.0389 - mae: 0.0389
Epoch 90/100
267/267 [==============================] - 0s 187us/sample - loss: 0.0383 - mae: 0.0383
Epoch 91/100
267/267 [==============================] - 0s 198us/sample - loss: 0.0384 - mae: 0.0384
Epoch 92/100
267/267 [==============================] - 0s 198us/sample - loss: 0.0377 - mae: 0.0377
Epo

...

267/267 [==============================] - 0s 235us/sample - loss: 0.0594 - mae: 0.0594
Epoch 9/100
267/267 [==============================] - 0s 208us/sample - loss: 0.0510 - mae: 0.0510
Epoch 10/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0585 - mae: 0.0585
Epoch 11/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0425 - mae: 0.0425
Epoch 12/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0382 - mae: 0.0382
Epoch 13/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0365 - mae: 0.0365
Epoch 14/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0378 - mae: 0.0378
Epoch 15/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0354 - mae: 0.0354
Epoch 16/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0361 - mae: 0.0361
Epoch 17/100
267/267 [==============================] - 0s 234us/sample - loss: 0.0352 - mae: 0.0352
Epoc

266/266 [==============================] - 0s 294us/sample - loss: 0.0375 - mae: 0.0375
Epoch 70/100
266/266 [==============================] - 0s 294us/sample - loss: 0.0368 - mae: 0.0368
Epoch 71/100
266/266 [==============================] - 0s 352us/sample - loss: 0.0363 - mae: 0.0363
Epoch 72/100
266/266 [==============================] - 0s 294us/sample - loss: 0.0343 - mae: 0.0343
Epoch 73/100
266/266 [==============================] - 0s 294us/sample - loss: 0.0345 - mae: 0.0345
Epoch 74/100
266/266 [==============================] - 0s 294us/sample - loss: 0.0363 - mae: 0.0363
Epoch 75/100
266/266 [==============================] - 0s 352us/sample - loss: 0.0353 - mae: 0.0353
Epoch 76/100
266/266 [==============================] - 0s 342us/sample - loss: 0.0354 - mae: 0.0354
Epoch 77/100
266/266 [==============================] - 0s 304us/sample - loss: 0.0355 - mae: 0.0355
Epoch 78/100
266/266 [==============================] - 0s 311us/sample - loss: 0.0390 - mae: 0.0390
Epo

267/267 [==============================] - 0s 293us/sample - loss: 0.0315 - mae: 0.0315
Epoch 30/100
267/267 [==============================] - 0s 293us/sample - loss: 0.0318 - mae: 0.0318
Epoch 31/100
267/267 [==============================] - 0s 293us/sample - loss: 0.0329 - mae: 0.0329
Epoch 32/100
267/267 [==============================] - 0s 351us/sample - loss: 0.0343 - mae: 0.0343
Epoch 33/100
267/267 [==============================] - 0s 293us/sample - loss: 0.0329 - mae: 0.0329
Epoch 34/100
267/267 [==============================] - 0s 293us/sample - loss: 0.0313 - mae: 0.0313
Epoch 35/100
267/267 [==============================] - 0s 333us/sample - loss: 0.0315 - mae: 0.0315
Epoch 36/100
267/267 [==============================] - 0s 295us/sample - loss: 0.0325 - mae: 0.0325
Epoch 37/100
267/267 [==============================] - 0s 316us/sample - loss: 0.0313 - mae: 0.0313
Epoch 38/100
267/267 [==============================] - 0s 293us/sample - loss: 0.0316 - mae: 0.0316
Epo

266/266 [==============================] - 0s 411us/sample - loss: 0.0353 - mae: 0.0353
Epoch 91/100
266/266 [==============================] - 0s 411us/sample - loss: 0.0340 - mae: 0.0340
Epoch 92/100
266/266 [==============================] - 0s 470us/sample - loss: 0.0362 - mae: 0.0362
Epoch 93/100
266/266 [==============================] - 0s 411us/sample - loss: 0.0360 - mae: 0.0360
Epoch 94/100
266/266 [==============================] - 0s 464us/sample - loss: 0.0386 - mae: 0.0386
Epoch 95/100
266/266 [==============================] - 0s 420us/sample - loss: 0.0358 - mae: 0.0358
Epoch 96/100
266/266 [==============================] - 0s 420us/sample - loss: 0.0360 - mae: 0.0360
Epoch 97/100
266/266 [==============================] - 0s 379us/sample - loss: 0.0422 - mae: 0.0422
Epoch 98/100
266/266 [==============================] - 0s 411us/sample - loss: 0.0367 - mae: 0.0367
Epoch 99/100
266/266 [==============================] - 0s 411us/sample - loss: 0.0358 - mae: 0.0358
Epo

267/267 [==============================] - 0s 491us/sample - loss: 0.0303 - mae: 0.0303
Epoch 51/100
267/267 [==============================] - 0s 426us/sample - loss: 0.0300 - mae: 0.0300
Epoch 52/100
267/267 [==============================] - 0s 425us/sample - loss: 0.0295 - mae: 0.0295
Epoch 53/100
267/267 [==============================] - 0s 410us/sample - loss: 0.0294 - mae: 0.0294
Epoch 54/100
267/267 [==============================] - 0s 410us/sample - loss: 0.0295 - mae: 0.0295
Epoch 55/100
267/267 [==============================] - 0s 468us/sample - loss: 0.0303 - mae: 0.0303
Epoch 56/100
267/267 [==============================] - 0s 410us/sample - loss: 0.0303 - mae: 0.0303
Epoch 57/100
267/267 [==============================] - 0s 410us/sample - loss: 0.0285 - mae: 0.0285
Epoch 58/100
267/267 [==============================] - 0s 410us/sample - loss: 0.0309 - mae: 0.0309
Epoch 59/100
267/267 [==============================] - 0s 423us/sample - loss: 0.0286 - mae: 0.0286
Epo

In [38]:
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Best: -0.002743 using {'neurons': 200}
-0.004683 (0.001000) with: {'neurons': 1}
-0.003844 (0.000654) with: {'neurons': 5}
-0.003233 (0.000826) with: {'neurons': 10}
-0.003676 (0.001489) with: {'neurons': 15}
-0.003232 (0.001060) with: {'neurons': 20}
-0.003089 (0.001204) with: {'neurons': 25}
-0.003024 (0.001244) with: {'neurons': 30}
-0.003630 (0.001313) with: {'neurons': 50}
-0.003018 (0.000624) with: {'neurons': 60}
-0.003051 (0.000867) with: {'neurons': 100}
-0.003335 (0.001489) with: {'neurons': 128}
-0.002743 (0.000604) with: {'neurons': 200}
-0.002941 (0.000954) with: {'neurons': 300}
